# Installing Libraries and Downloading Models

In [11]:
%pip install pandas
%pip install -r rouge/requirements.txt
%pip install rouge-score
%pip install scikit-learn
%pip install spacy

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
ERROR: Could not open requirements file: [Errno 2] No such file or directory: 'rouge/requirements.txt'
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.
Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [12]:
!python -m spacy download en_core_web_sm

Defaulting to user installation because normal site-packages is not writeable
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 24.7 MB/s  0:00:00 eta 0:00:01
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


# Text Classification

For the text classification process, the following libraries are used:
- **Pandas** is used to read the CSV file containing the dataset, as well as temporarily hold it in memory, before they are parsed into the format used by spaCy.
- **Scikit-learn** has methods that are used to split the data, using `train_test_split`, as well as generate the metrics used to evaluate the performance of the text classification process, using `accuracy_score` and `classification_report`.
- **SpaCy** is used to create the text classification pipeline, as well as utility classes that helps with the analysis of the performance of the text classification process.

In [ ]:
import pandas as pd
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split
import spacy
from spacy.training import Example

The first step in the text classification process is the creation of a blank spaCy pipeline. This is done through the use of spacy's `blank` method. As well as creating a blank pipeline, it also loads the specified language class. In this case, it loads the English language class.

Once the pipeline is created, the `textcat` component is added through the `add_pipe` method. It takes in the name of the component being added. In this case, the given name `textcat` corresponds to the `TextCategorizer` pipeline component which attempts to analyze a given text and predict if it is a given category or not.

Once the pipeline component is created, the two labels that will be used to classify the documents are added to the `TextCategorizer` component. In this case, the labels `SPAM` and `HAM` are used, which is used to categorize if a given Short Message Service (SMS) message is considered spam or not.

In [14]:
nlpTC = spacy.blank("en")

textcat = nlpTC.add_pipe("textcat")
textcat.add_label("SPAM")
textcat.add_label("HAM")

1

For this implementation a subset of the [`ucirvine/spam_sms`](https://huggingface.co/datasets/ucirvine/sms_spam) dataset is used. The dataset, which is a collection of SMS messages with corresponding labels indicating if they are spam (value of `1` in the `label` column) or not (value of `0` in the `label column).

Said subset is saved in the provided `sms_subset.csv` file and is loaded through pandas' `read_csv` method. The method takes in the filename of the CSV file and it loads it into a `DataFrame`.

Once the dataset is loaded, it is converted into the format that is understood by spaCy. This process is done through the list comprehension feature of the Python language. What this does is it iterates through all the rows, using a DataFrame's `iterrows` method. During iteration, the `iterrows` method returns the index, which in this scenario is unused, and the current row.

The values in this row is then used to make a tuple containing two values. The first value is simply the text value, found in the row's `sms` column. The second value in the tuple is a dictionary, with the `cats` attribute. The `cats` attribute contain another dictionary that contains all labels that is used to categorize the text.

In this implementation, there are two labels. One is for `SPAM` and its value is derived on the value of the `label` column of the row. If the value in the `label` column is 1, then the `SPAM` label is set to 1, and it is 0 if otherwise. The other label is `HAM` which indicates if the text is not spam. Its value is also derived from the `label` column of the row, though it is subtracted to 1, thereby flipping the actual value. If the value of the `label` column is 1, then the `HAM` label is set to 0, and if the value of the `label` column is 0, then the `HAM` label is set to 1.

In [ ]:
df_data = pd.read_csv('spam_sms.csv')

data = [
  (row['sms'], {'cats': { 'SPAM': int(row['label']), 'HAM': 1 - int(row['label']) }})
  for _, row in df_data.iterrows()
]

Once the data has been converted to spaCy's format, it is then split into training and testing data. This is done with scikit-learn's `train_test_split` method. It takes in the following arguments:
- **data** is the data being split into training and testing data.
- **train_size** is the ratio of how much of the whole dataset will be put into the training data.
- **random_state** is the seed used to make the random splitting of data deterministic.

In this case, 80% of the data is put into training data, while the remaining 20% is put into the testing data, which will be used when evaluating the performance of the model when encountering unseen data. The `random_state` is set into an arbitrary number, and can be set into another value to experiment on how the splitting of data can affect the performance of the process.

In [16]:
train_data, test_data = train_test_split(data, train_size=0.8, random_state=42)

Before the model can be trained, it has to be initialized first. This is done with the language pipeline's `initialize` method. This method returns the Stochastic Gradient Descent optimizer that will be used by the pipeline.

In [17]:
optimizer = nlpTC.initialize()

This is the part where the text classification model is trained. Firstly, the training data is iterated through, with the text and the categorical annotations referenced separately.

For each entry in the training data, an `Example` is created. An `Example` is a spaCy class that contains two `Doc`s, one that is `generated` by the model, and one that is the `reference` to the gold standard of the data entry.

In this scenario, the `Example` is made using the static `from_dict` method, which takes in a generated `Doc` and a subset of the reference `Doc` with a dictionary. In this case, the generated `Doc` is made by passing the `text` value into the language pipeline's `make_doc` method. The passed `annotations` dictionary contains the categories indicating if the given text is spam or not.

Once the `Example` is created, it is passed to the language pipeline to train the `TextCategorizer` component. This is done with the pipeline's `update` method. This method takes in a list of examples that will be used to train the model. In this case, the single `Example` created is passed in a list. As well as the examples, the SGD `optimizer` is also passed to the model.

In [18]:
for text, annotations in train_data:
  example = Example.from_dict(nlpTC.make_doc(text), annotations)
  nlpTC.update([example], sgd=optimizer)

To test if the text classifier works as intended, a sample SMS message is fed to the pipeline. This is done by simply invoking the object storing the pipeline. This operation returns a generated `Doc` that contains the annotations generated by the pipeline, stored in the `Doc`'s `cats` attribute.

This `cats` is a dictionary that has the two labels added to the `TextCategorizer` component, which is `SPAM` or `HAM`. The value of the two labels are the predicted probability that the text is spam or not.

It can be understood that the label with the higher probability is the predicted label of the text, though experimentation of the accepted threshold can be done to better improve the performance of the model.

In [19]:
print("Sample Prediction Output with probabilities:")
doc = nlpTC("Congratulations! You just won a million dollars. To claim your earnings, please send us your credit card number along with your name, address, and the three digit code at the back of your card.")
print(doc.cats)

Sample Prediction Output with probabilities:
{'SPAM': 0.09895423799753189, 'HAM': 0.9010457396507263}


The `classify_sms` function is defined. This accepts an argument `sms` which is the text that will be classified if it is spam or not.

The function first takes the `sms` argument and passes it to the pipeline to be classified. This returns a `Doc` that contains the predicted probabilities of each labels, indicating how likely the given SMS message is of being `SPAM` or `HAM`. These values are accessed through the `Doc`'s `cats` attribute and each value is stored in their respective variables.

These values are compared, where if `spam_score` is greater than `ham_score` then the function returns `"SPAM"`, else it returns the string `"HAM"`.

In [20]:
def classify_sms(sms):
  doc = nlpTC(sms)

  spam_score = doc.cats['SPAM']
  ham_score = doc.cats['HAM']

  if spam_score > ham_score:
    return "SPAM"
  else:
    return "HAM"

This continuously prompts the user for a sample SMS message that will be classified with the training model. This is done with Python's built-in `user_input` method. If the user enters `exit`, the while loop `break`s and it stops executing. If the loop did not stop, the text entered by the user is fed to the NLP pipeline and classified if its spam or not. The result of the prediction is printed and displayed to the user.

In [21]:
while True:
  user_input = input("Now, enter a new sample SMS message for classification (or type 'exit' to quit): ")
  if user_input.lower() == 'exit':
    break

  classification = classify_sms(user_input)
  print(f"The email is classified as: {classification}")

This cell defines the evaluate function for the sentiment analysis section. It takes a dataset of texts and their annotations, creates spaCy `Example` objects for each, and compares the predicted labels to the reference labels. The function then prints a classification report showing the model's performance metrics, such as precision, recall, and F1-score.

In [22]:
def evaluate(data):
  examples = [Example.from_dict(nlpTC(text), annotations) for text, annotations in data]
  y_true = [1 if example.reference.cats['SPAM'] > example.reference.cats['HAM'] else 0 for example in examples]
  y_pred = [1 if example.predicted.cats['SPAM'] > example.predicted.cats['HAM'] else 0 for example in examples]

  print("Classification Report:\n", classification_report(y_true, y_pred))

The previously defined `evaluate` function is ran on the test_data. This displays the performance of the model when fed with unseen data.

In [23]:
print("Testing Data Performance:\n")
evaluate(test_data)

Testing Data Performance:

Classification Report:
               precision    recall  f1-score   support

           0       0.88      1.00      0.93        21
           1       1.00      0.84      0.91        19

    accuracy                           0.93        40
   macro avg       0.94      0.92      0.92        40
weighted avg       0.93      0.93      0.92        40



# Part-of-Speech Tagging

For the part-of-speech tagging process, the following libraries were used:
- **SpaCy** is used for its `Tagger` pipeline component, which is included and pre-trained in its `en_core_web_sm` model.
- **SciKit-Learn** is used for its metrics generation methods, specifically its `classification_report` method that neatly generates a model's Accuracy, Precision, Recall, and F1-Score.

In [24]:
import spacy
from sklearn.metrics import classification_report

The first step in the part-of-speech tagging process is the loading of the language pipeline. `en_core_web_sm` is a pre-trained pipeline for the English language which includes the pipeline components `tok2vec`, `tagger`, `parser`, `senter`, `attribute_ruler`, `lemmatizer`, and `ner`.

For the purposes of this implementation, only the results of the `tagger` component will be analyzed, but the effects of the other components are included in the generated `Doc` object.

In [25]:
nlp = spacy.load('en_core_web_sm')

The `analyze_text` function is defined. This accepts an argument text` which is the text that will be analyzed and part-of-speech tagged.

The function first takes the `text` argument and passes it to the loaded pipeline. This call returns a `Doc` which contains the text that has been tagged by the pipeline. These tages has been stored in each token's `pos_` attribute.

To get the list of POS tags, the tokens in the generated document is iterated through and is processed by Python's list comprehension feature. The token's `text` and `pos_` attribute is extracted and saved in a tuple. This is done for all tokens found in the text. This list of tuples are then returned by the function.

In [26]:
def analyze_text(text):
  doc = nlp(text)
  pos_list = [(token.text, token.pos_) for token in doc]
  return pos_list

The `evaluate` function is defined. This function takes two arguments:
- `text` is the text that will be fed to the pipeline and will be used to evaluate the model's performance.
- `y_true` is a list of POS tags that will serve as the _gold standard_ data, which will be used to analyze the model's performance.

The function takes the `text` argument and passes it to the loaded pipeline to get it part-of-speech tagged. The resulting `Doc` object contains the tagged tokens, which is then put into a list using Python's list comprehension feature.

The resulting is compared to the provided `y_true` list of POS tokens which is used to create a classification report. The classification report contains the precision, recall, and F1-score of each POS tag, along with the overall accuracy of the whole result.

In [ ]:
def evaluate(text, y_true):
  doc = nlp(text)
  y_pred = [token.pos_ for token in doc]

  print('Classification Report\n', classification_report(y_true, y_pred))

The `evaluate` function is then used to generate a classification report for the given text data. The given text, and its corresponding POS tags, is selected from an entry in the Universal Dependencies [English Web Treebank](https://github.com/UniversalDependencies/UD_English-EWT), which is the gold standard data source for POS tagging.

In [28]:
evaluate(
  'These are 1) Assassinate or overthrow Gen. Pervez Musharraf, the Pakistani military "president" who had made a coup in 1999 and has thrown in his lot with the United States against the Taliban and al-Qaeda.',
  ['PRON', 'AUX', 'NUM', 'PUNCT', 'VERB', 'CCONJ', 'VERB', 'PROPN', 'PROPN', 'PROPN', 'PUNCT', 'DET', 'ADJ', 'ADJ', 'PUNCT', 'NOUN', 'PUNCT', 'PRON', 'AUX', 'VERB', 'DET', 'NOUN', 'ADP', 'NUM', 'CCONJ', 'AUX', 'VERB', 'ADV', 'PRON', 'NOUN', 'ADP', 'DET', 'ADJ', 'PROPN', 'ADP', 'DET', 'PROPN', 'CCONJ', 'PROPN', 'PUNCT', 'PROPN', 'PUNCT'],
)

42
Classification Report
               precision    recall  f1-score   support

         ADJ       1.00      0.33      0.50         3
         ADP       0.75      1.00      0.86         3
         ADV       0.00      0.00      0.00         1
         AUX       1.00      1.00      1.00         3
       CCONJ       1.00      1.00      1.00         3
         DET       1.00      1.00      1.00         4
        NOUN       0.75      1.00      0.86         3
         NUM       1.00      1.00      1.00         2
        PRON       1.00      1.00      1.00         3
       PROPN       0.78      1.00      0.88         7
       PUNCT       1.00      0.83      0.91         6
        VERB       1.00      1.00      1.00         4

    accuracy                           0.90        42
   macro avg       0.86      0.85      0.83        42
weighted avg       0.90      0.90      0.89        42



/home/djcayz/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/home/djcayz/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])
/home/djcayz/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:1731: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", result.shape[0])


# Sentiment Analysis

For the sentiment analysis process, the following libraries were used:
- **Pandas** is used to load the testing data that will be used to evaluate the performance of the sentiment analysis model.
- **random** is a built-in Python module that provides pseudo-random number generation features. For the purposes of this implementation, it was used to shuffle the training data between each generation of training the model.
- **SpaCy** is used for its `TextCategorizer` pipeline component, which will be trained to predict the sentiment of a given component.
- **SciKit-Learn** is used for its metrics generation methods, specifically its `classification_report` method that neatly presents a model's Accuracy, Precision, Recall, and F1-Score.

In [1]:
import pandas as pd
import random
import spacy
from sklearn.metrics import classification_report
from spacy.training import Example

To initialize the sentiment analysis process, a blank spaCy pipeline is created using the library's `blank` method. The `en` identifier is specified to signal that the English language pre-trained model will be used as the base for the pipeline.

Once the blank pipeline is created, the `TextCategorizer` pipeline component is created and added to the pipeline using the pipeline's `add_pipe` method. As well as the creation of the pipeline component, the labels `POSITIVE` and `NEGATIVE` are specified to the component. These will serve as the labels that will be predicted from the given text data.

In [2]:
nlp = spacy.blank("en")

textcat = nlp.add_pipe("textcat")

textcat.add_label("POSITIVE")
textcat.add_label("NEGATIVE")



1

The training data that will be used by the model is established. It is a list of tuples, where the first element is the text, and the second is a dictionary where `cats` is another dictionary that contains the labels that indicate if the text is `POSITIVE` or `NEGATIVE`.

In [3]:
train_data = [
  ('When this film was made, the hippie thing had gone mainstream. The ideas of the counter culture was well established, that is why such a big film could be made. Yet it has something to say, and it is said really beautifully. Apart from those who\'re only waiting for the wanking material, this film is given credit for its beautiful scenes(which in itself is more than enough reason to see the film) by the most. The soundtrack to this film, which actually became more popular than the film itself, is another plus. Pink Floyd\'s "Careful with that axe Eugene" suits really well with the explosions, the absence of music in other scenes gives the film a nice quiet mood. But. It seems as though the messages in this film have been overlooked by the most. If you didn\'t understand it, which seems to be the case for the most, I\'ll give you some hints: The man(tough guy, what ever his name is-Mark?) is a part of a "reality group". He leaves this group saying something like "I\'m willing to die. But not of boredom" He later go for a joyride with a stolen plane, probably to seek some action. As he is in the air, Grateful Dead\'s Dark Star(from the Live/Dead album) is played(i think). This song contains the phrase "Shall we go you and I while we can", this is though not heard in the film.(Perhaps stretching it a bit too far meaning that quote is essential?) In the plane, he checks up a girl(Daria), who is driving in her car to a conference(about giving typical suburban families the opportunity to live in a super-relaxing place in the desert, where everything is so simple and nice. For the whole family!), by diving down, almost hitting the car. He lands the plane, and joins the girl on her way to Detroit. They stop at Zabriskie point, where they enjoy each other as living creatures and the nature. Later a family with a big car(of the type which you sleep in) and a speed boat is showed visiting Zabriskie Point, the father saying something like "what a waste driving all the way up here", and the kid sitting inside the car, grinning. I sensed a "this wasn\'t much better than on the telly"-attitude. Daria takes Mark back to the plane which now is painted in a psychedelic style, with the identity number changed to "no war" on one side and "no words" on the other. "Bucks Sucks" is also written on the plane. Mark takes the plane back to where he stole it from, saying to Daria before he leaves "I don\'t risk anything" or something, one of several hints about he not caring too much about his destiny. (This because he has the feeling that the environment that surrounds don\'t give him anything- "I wonder what happens in the real world") On the airport he is met by police officers who shoots him even though he just has returned the plane. Daria hears this on the radio, but decides to go to the conference in the fancy mansion. Here she feels alien after the adventures with her just killed friend. She enjoys fresh water running down a rock, more than the swimming pool. Inside the house the viewer is once again given a hint about anti-materialism -She looks out through a glass wall, holding her hands on the glass like she was trapped. The business men is seen arguing, the one side eager to make a big deal, the other afraid of losing money. Daria leaves the house and looks back at it, visualizing it blowing up. After the house, several other things blow up, for example a television. She smiles, happy she has inside herself destroyed what she after the meeting with Mark look upon as something negative.<br /><br />To summarize: Mark obviously experience the "reality group" as not very useful as they just sit and talk, taking no action. He clearly has bad feelings about things being as they are, and it seems like he feels that it\'s no use fighting against it. He wants to leave. He helps Daria, who is "in mind but not in action" seeing his point of view. Where his feeling of being misfitted turns out leading to his death, one can hope Daria uses the ideas in a way that will turn out more constructive. In the film you see how a town (LA) is being polluted by commercial (too bad you have to show the commercial to make the point), you see business men deciding what is the future, et cetera, and you see people being unhappy with these and other situations which is parts of the modern world.<br /><br />I have only seen the film once, so I have not caught all points, but I certainly got a feeling of what this film has to say, and I find it strange that this film can be called meaningless. If you say the points are being too obvious, I can see why, this film probably intended to appeal to the post-hippie radicals "digging" the thoughts of anti-establishment. Even though, it has a lot to say, and its message is still needed today, things pretty much evolving in the same direction as it did before the sixties. Zabriskie Point is a really great film, telling a story about quite normal young people (not far out hippies tripping around tip toe on acid, digging everything) seeking what they percept as real, dissatisfied with the conventional. And it is done in a truly beautiful way.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I saw his film at the Ann Arbor Film Festival. I am a film student at the Univeristy of Michigan so I know a thing or two about film. And Crispin Glover\'s film is outrageous. He basically exploits the mentally challenged. Not only is Shirly Temple the anti-Christ (which I admit is a little funny) telling the mentally challenged to kill each other, but there is an obsession with killing snails. Crispin also plays with the idea of being in love with one of his actors who is as they all are, mentally challenged. PETA and Human Rights should be all over this thing. It\'s not \'counter-culture\' as Crispin stated at the Ann Arbor Film Festival, it\'s exploitation.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Let\'s get some things straight first: Zombies don\'t exist so the filmmaker can have them WALK, RUN, hell even FLY if he wants to. That\'s what makes this original Zombie movie so good. Everything they did was so damn original. I hate it when filmmakers do everything like Romero or when fan boys expect everything like Romero. Some idiots think that zombies should only growl like a typical Romero movie, once again zombies don\'t exist so a filmmaker can make zombies whistle if he wants. The zombies in this movie all look very good but OBVIOUSLY they are not decaying corpses since they JUST freaking died! They are pretty messed up though and full of chopped faces and blood. One of the coolest scenes was a half eaten cat. It looked so damn real my daughter cried when she saw it. This movie got really good reviews in Fangoria and Rue Morgue so that made me want to go see it. I\'m glad I listened. They are always right when it comes to real horror fan\'s tastes. 10 out of 10! Go rent it!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I love Seth Green. His appearances on THat 70s\' Show is always worth watching but last night, I felt the show needed to overhauled. Four single young guys inherit a New York City apartment that most of us would die for. The grandmother must have been an heiress to have such space in the first place. So I felt the need for realism should have been brought out. Anyway the plot about four best friends getting this apartment was not believable. I would have been thrilled if they had to move in with one of their parents which would have provided great humor and dysfunctional about the show\'s set up. There did not seem to be much humor in it. I am only watching it because it falls before My Name is Earl on a winning Thursday night. I think they should go back, scrap this series, and start over. We need more family involved series. How about Seth and his friends move in with his wacky parents in the suburbs after a fire burns their place down. THey could have Dabney Coleman play the father and Christine Estabrook, play the mother and dysfunctional siblings. The list of possibilities with somebody like Seth Green are endless and the network is blowing it.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('"Three Daring Daughters" is a sickly sweet, rose-colored look at divorce, remarriage, and single-parent living. Obviously, social issues and economic difficulty have no place in the picture perfect life of a single parent mother who feels exhausted, takes a cruise, and then dates and marries a band conductor. Even when the "its just a movie" phrase excuses the script from addressing real-life problems, \'Daughters\' suffers from too many incoherent high-note songs, children whose personalities are not based on real children and band leader Hose Iturbi playing himself. Isn\'t it bizarre that any real person would star in a film in which their supposed real self gets married? <br /><br />Admittedly, this movie was released in the nineteen forties. Only a love for old style Hollywood romance and comedy could make \'Daughters\' a tolerable film.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I will start by saying that this has undeservedly be panned by just about everyone! The fact is it wasn\'t what anyone was expecting, especially from Guy Ritchie. What everyone was expecting was cockney geezers and good one liners "do ya like dags?" etc, but this is far more mature than his previous works. I would agree that it is confusing but all the facts are there for us we just have to see them and listen harder, this film demands all your attention! Look past the cool and dazzling look of the film, try to listen to the dialogue rather than admire the performances and i think we will all get a more thorough understanding of the whole film.<br /><br />Yes this has its influences from modern classics( fight club, pulp fiction etc ) but it is in the whole original in both direction and pacing with a music score second to none. I feel that if everyone watched this film over and over they would understand it a lot more and maybe appreciate it for the fine piece of modern cinema that it is and i hope also that Ritchie continues in this vain as i far prefer this to his mockney "masterpieces".', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I cheer for films that fill in subject matter gaps in world cinema. So after watching the trailer for "Water Lilies," I expected to like this film because I thought I\'d stumbled on something unique: a movie that honestly portrays teen lesbian love - sort of a female version of "Beautiful Thing." <br /><br />The main characters are young French women 15 years old. Marie is slender, reticent and pretty in a tomboyish way; Floriane is outgoing, athletic and beautiful; and Anne is loyal, pudgy and behaviorally immature. The erotic interrelationship between Marie and Floriane is always simmering in this movie, if not at the surface, then just below it. <br /><br />"Water Lilies," however, is not about the dawning of lesbian love upon two teens; it is about sexual frustration, suffering, ennui, teens working at cross-purposes and - in at least two instances - joyless, mechanical sex. It also proves that screenwriters and film-makers mar their own creations when they become too manipulative.<br /><br />In the extra features on the "Lord of the Flies" DVD, director Peter Brook says, "French cynicism starts with the arousal of sex," meaning the French regard children as angels while they regard adolescents and adults with a pervasive cynicism. Part of the downfall of this film is film-maker Celine Sciamma has gulped a mighty dose of this cynicism.<br /><br />"Where is the joy?" I asked myself while watching this film. Yes, first love can be painful and frustrating, but it can also be joyful and triumphantly erotic in a fresh, life-affirming way. These positive aspects are missing from this movie; there is no balance.<br /><br />Organically, this movie wants to be a poignant celebration of first love. But Sciamma is too impressed with her own cynicism and cleverness and ruins the film. First, what is the point of showing only the plump girl nude? I know there is an established tradition of tasteful teen nudity in European cinema, as evidenced by films like "The Slingshot; The Rascals; The Devil, Probably; The Little Thief; Murmur of the Heart; Friends; Beau Pere" and "Europa, Europa"; but this instance is a petty authorial intrusion - "See, audience, I can make a film where I show only the unattractive person nude." Either no nudity or evenly distributed nudity would\'ve been an honest way to go.<br /><br />There is a scene in a club where Floriane and Marie are dancing. What follows next is not just Floriane cynically manipulating Marie; it is film-maker Sciamma cynically manipulating her audience.<br /><br />Perhaps the biggest betrayal of authenticity and organic honesty takes place when Floriane warns Marie she\'s about to request something that is "not normal." Marie understandably asks, "Who cares about being normal?" Then Sciamma plays false with her audience and the hurtling momentum of the movie, because Floriane\'s request is a phony, derivative and substitute question - not the authentic, heartfelt question the movie, Marie\'s character and the viewers who\'ve invested their time deserve. <br /><br />Here are also two moments which clank falsely on the viewer\'s nerves: 1) Since when do the French - of all people - take baths wearing bathing suits, and with a turtle to boot? 2) What teen - of any nationality - would chomp down on an apple core that\'s been thrown in the garbage in order to get a taste of the beloved\'s mouth?<br /><br />The three main actresses are promising and, if they find better vehicles for their talents, may become excellent actors. Louise Blachere (Anne) is the best actress in terms of technique and could have a successful career in supporting roles. Adele Haenel (Floriane) could become a leading lady, or a bombshell, or both. Pauline Acquart (Marie) possesses an intensity and magnetism which are unmistakable. In the future, she could play everything from an emotionally crippled librarian to a mysteriously sensual seductress to a reluctant politician riding a meteoric rise in acclaim.<br /><br />All in all, "Water Lilies" was very disappointing. Will an honest film-maker please make an authentic movie about two young women falling in love! No - not necessarily for the sake of this middle-aged guy - but so young lesbian girls can have something of quality they can watch and identify with. And yes, to fill a subject matter gap in world cinema.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie will promote the improvement of the mind. Read a book! It\'s incredible anyone would think this movie deserved the time and investment to make. I\'ve seen "B" movies before but the "C" movie has just been invented. I didn\'t think I would ever enjoy Power Rangers since my kids stopped watching but I found myself looking for the videos fifteen minutes into "Knights." High school productions are better than this and the actors involved should erase this from their resume. Embarrassment is one of many descriptions that come to mind. My roommate, who loves these types of movies even turned it off. Now that has to really tell you something. If you watch this movie, and like it, I will pray for you.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Well, I bought the Zombie Bloodbath trilogy thinking it would be mindless gory fun. That\'s what it is, without the fun. This film truly is mindless, it is absent of any plot or character development, or any sort of storyline. The basic problem with this movie is the kills and gore. Basically, every kill looks EXACTLY the same. ZOmbies ripping someone apart. Yeah, that\'s okay, but you need some original kills too. I mean it got really lame, every kill looked exactly the same, filmed exactly the same way. Thats what killed me. I love gore, and the gore in this film did nothing for me. It was just boring. No storyline, just the same lame scene over and over again with a different person. I wanted to like this movie, too. I love shot on video gore movies...like Redneck Zombies. But I couldn\'t kid myself. This film has it\'s good points, but none of those are in the film. I understand that many of the "zombies" helped out with the flood and there were like over 100 zombies, which is pretty cool how they got so many people involved and helped out in the world. But overall, this is a terrible film.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('"Dressed to Kill" has been more or less forgotten in critical circles in the past 20 years, but it is a true American classic, a film which is much more than just a glossy thriller.<br /><br />I sincerely hope the DVD release will give more people the chance to hear about it and see it.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Besides the fact that my list of favorite movie makers is: 1)Stanley Kubrick 2)God Allmighty 3)the rest... this movie actually is better than the book (and the TV miniseries though this is an easy feat, considering the director). The flawless filming stile, the acting and (Kubrick\'s all time number one skill) the music - make it THE masterpiece of horror. I watched the TV miniseries a few years ago and liked the story and I had my hopes about this when I got a hold of it. IT BLEW ME AWAY!!! It is far better than I ever imagined it. It starts slow (Kubrick trademark) and has a lot of downtime that builds up the suspense. The intro scene is a classic by all means and I watched it about 20 times just for the shear atmosphere it induces to the whole film. Also the film doesn\'t offer a lot of gore (it has just enough and it is by no means tasteless) a trend that I hate in recent day horror films. Just watch it!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('The story has been told before. A deadly disease is spreading around... But the extra in this film is Peter Weller, his interpretation of Muller on the run is real. He is indeed a desperate person just going home to see his child. This person could be working next to you.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('"Gespenster" Question of to be cool in the German cinema<br /><br />There are not many German films in the last ten years, who have made me so interest. Yes, the problem of the most German films are in this film "Gespenster" too. He is on some places to uncooked to be good to see. Special the figure of Toni (Sabine Timento) is too cool. But thats is in German films always so. Everybody must to learns this coolneß - is the realism in this films. Thats difficult to understand. But in this case it makes some sense, because she steals and she lies - she is the kind of girl is better you never love it, because you lose it. Thats not clear for the other girl Nina in this film. She love her - and she would lose her. But Nina lost everything. She will play with soft emotion and a sad feeling. There is no way - but you must take it said Herbert Achterbusch for twenty years. Thats so often the way it goes in German films. Why? Nina (Julia Hummer) is not inside of the laws of society - the is outside - and there she have no chance. This films tries not on every place to gave her a part inside. Thats one of the problems - the stupid break with conventions - the criminal fascination. Throw it all away - and go nowhere! But the actress plays this difficult part very interesting. On the other side - there the parents - who are the pendant to the two girls. The have a car - a hotel suite - the have money and live in world with music of the opera. But the film stand always in some distance to seem. There is no much explaining of them.<br /><br />In the center of this film, there is one scene you will never forget. The two girls got to a casting. And there they should say how they find together. In this scene Toni will lying on. She said a fantastic story-has nothing to do with her. And then Nina will say the truth. She said it in an introversion way. There is no exhibition in it. She looks to the bottom and said what will happened for here. Thats a great moment. In the next scene on the party with pictures in red this feeling is going on- than Toni goes away...<br /><br />Okay, The film will end - in the German way of coolneß - rubbish - here the circle of sadness is closing. But there was a moment - where is happening something else - and this moment was important. He is more than German coolneß - and this moments are rare in the German cinema in this time!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I have to start off by apologizing because I thought the first 75-80% of this film was hilarious. It\'s mostly because of Brad Pitt\'s performance. Spot on.<br /><br />The acting by all involved was quite good but Brad stole the movie. The atmosphere was perfect in all respects. I\'m not a giant Pitt fan but this has got to be one of his best roles ever.<br /><br />Brutal,Honest,Gritty. All good words to describe this movie.<br /><br />I was reading a previous review and the person said that the reasoning behind Early\'s violence isn\'t explained. It is explained but they thankfully don\'t have to go into graphic detail to get their point across.<br /><br />Overall I gave this a 9 because every scene bar 1 or 2 was effective. I think the humor in the first half or so is perfect for this movie. Underrated.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I first saw this when it was picked as a suggestion from my TiVo system. I like Danny Elfman and thought it might be interesting. On top of that, I\'m a fan of Max Fleischer\'s work, and this started out with the look and feel of his 30s cartoon. With both of those, I thought it would hold my interest. I was wrong. Just a few minutes in, and I had the fast forward button down. I ran through it in about 15 minutes, and thought that was it.<br /><br />Afterwards, I read some of the other reviews here and figured I didn\'t give it enough of a chance. I recorded it again and watched it through. There\'s 75 minutes of my life I\'m not getting back.<br /><br />I can\'t believe there aren\'t more bad reviews. Personally, I think it\'s because it\'s hard to get to the 10 line comment minimum. How many ways are there to say this is a waste of time?<br /><br />The movie comes across as though it was made by a few junior high kids ready to outrage the world and thinking they can with breasts, profanity, and puke jokes. The characters are flat. The parody of "Swinging the Alphabet" is lame, essentially cobbling the tune, getting through A - E, hitting the obvious profanity a "F", and then having no idea where to go. The trip through the intestines to the expected landing doesn\'t work the first time, let alone the following ones. <br /><br />Across the board, the entire movie is what you would expect from someone trying to "out-South Park" Stone and Parker without the ability to determine what is and isn\'t funny. This might be amusing if you\'re high. Otherwise, it\'s not.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Probably Bigas Luna\'s finest achievement for it achieves a delicate balance between sleaze, eroticism and surrealism. The delicious Mathilda May, who spent most of Tobe Hooper\'s "Lifeforce" in the buff, is the object of young Biel Duran\'s pre-teen lust. He can\'t get May\'s breasts out of his mind and wants so badly to suckle them and suckle the breasts of his own mother, too. His pursuit of May IS the film. As in Luna works such as "Lulu" and "Jamon! Jamon!", the director brings a slightly warped sexual sensibility to his strange but beautiful tale. The usual suspects will be offended, but those with open minds will enjoy this frothy erotic poem to the female breast. José Luis Alcaine\'s images are gorgeous and Nicola Piovani\'s score is sweet and rich. A gorgeous cinematic confection with a delightfully anarchic sensibility that the Spanish do so naturally.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Nicole Eggert was listed as the star of this, despite Micheal Dorn & Stacey Keach being much bigger stars than her.<br /><br />Basically this is a bit of a spin on the "Alien lands on Earth" film. Eggert plays the girl who feels sorry for an Alien being chased by the military and takes in the runaway creature in her very sexy disguise. A bit of nudity and partial nudity, a pointless sex scene all feature along the way.<br /><br />The film stumbles through a few obvious set-pieces and running jokes about being shown photographs. I quite liked the Star Trek jokes when Micheal Dorn had been taken over and he got a really cool death scene.<br /><br />It was fairly obvious that Stacey Keach was going to be taken over and the film had quite a weak ending, it would have been nice to show exactly what kind of talent the Alien passed to Eggert.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Tales from the Crypt: And All Through the House starts on Christmas Eve as Elizabeth (Mary Ellen Trainor) kills her husband Joseph (Marshall Bell), she drags his body outside ready to throw it down a well but while doing so misses an important news bulletin on the radio that says a homicidal maniac (Larry Drake) dressed as Santa Clause has escaped from a local mental asylum & has already killed several women with Elizabeth next on his list but she has other ideas & tries to turn the seemingly dangerous situation to her advantage...<br /><br />This Tales from the Crypt story was episode 2 from season 1, directed by the one of the show\'s regular executive producers Robert Zemeckis And All Through the House is a decent enough watch. The script by Fred Dekker was actually based on a story appearing in the comic \'The Vault of Horror\' & was originally adapted to film as one episode from the Britsih horror anthology film Tales from the Crypt (1972) which starred Joan Collins as the murderous wife character here played by Ellen Trainor. This particular version is good enough but doesn\'t do anything different or special & is a bit too linear & predictable to be considered a classic. At only 25 minutes in length it certainly moves along at a good pace, the story is just about macabre enough & it generally provides decent entertainment & I quite liked the downbeat ending. This time there are Christmas themed opening & closing Crypt Keeper (John Kassir) segments complete with the usual puns.<br /><br />Director Zemeckis does a good job & there\'s a nice winterly atmosphere with a hint of Christmas influence as well. There\'s not much gore here, someone has a poker stuck in their head, someone\'s face is cut with an icicle, someone\'s arm is cut with an axe & there\'s some blood splatter but generally speaking it\'s not that graphic. The acting by a small cast is pretty good.<br /><br />And All Through the House isn\'t the best tale from the crypt but it\'s a decent one all the same, worth a watch but after the comic book story & original 1972 film version did we really need or even want this?', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I recently watched the \'54 version of this film with Judy, and while i appreciated the story and music, i found that the film failed to hold my attention. I expected the \'76 remake to be the same story, except with a Barbra twist. I was pleasantly surprised - it was a much more realistic and modern look at fame, money, love and the price of it all. This version is so much more real than the \'54 one, with arguably better music, better acting, a more gripping plot line, and, of course, a deeper love. I do not understand why the previous film is on the American Film Institute\'s top 100 list, while this gripping remake fails to make a mark on any critic\'s list.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Okay, that was a pretty damn good episode. Much better than the credit it receives.<br /><br />The camera work is splendid. Best yet. I love that final shot. The atmosphere is fantastic, the costumes are great and the guest cast (minus the helpless victims) is strong. <br /><br />What I don\'t like about this episode is that many things that are left unexplained. why does it change sex? what\'s the purpose? and they\'re aliens? what kind? why were they never shown again in the later mythology?<br /><br />I\'m giving this episode a high THREE stars. One of my favorites yet, but the plot holes bother me. Still... not gonna let it ruin my entertainment.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('My husband and I enjoy The DoodleBops as much as our 8 month old baby does. We have bought him DVD\'s and CD\'s just so we can watch and listen to them ourselves. They are fun, energetic, and very entertaining. They encourage children to be active, share and care. They always have a positive message along with fun entertainment. Every time our son hears the theme song he quickly turns his head toward the television and starts bouncing up and down in excitement. Dee Dee is a wonderful singer, she has a great voice. Moe is a great dancer. I would recommend The DoodleBops to anyone with children. Our favorite song is The Bird Song. You just can not help but smile and want to dance when you hear it.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('When it comes to movies, I am generally easily entertained and not very critical, but must say that this movie was one big flop from the start. I gave it 30 minutes and then rewound it. What a waste of some great talent! I was very disappointed with this movie, as it was not what I expected.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('The action in this movie beats Sunny bhai in Gadar. Akshay Kumar possess the superpowers of Leonidus in 300, Neo in Matrix along with Spiderman and Superman. It is hilarious. Except for the typical Akshay Kumar and Anil Kapoor comedy I cannot see anything positive in this film. The story looks like the writer told his 10yr old son to write. The movie is so unreal that Anil Kapoors long range shooting with a shotgun is the least most mistake by the director. Except for the directors Tashan to make this movie there is no other Tashan. I regret wasting my money on this movie and I would not recommend it to anybody. 1/10 is the least I can give on IMDb or I would give it a zero.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This is far more than the charming story of middle-aged man discovering the pleasures of ballroom dancing (although it IS that as well). It\'s the tale of one person learning to love life again, pushing past all the pressures of work and money to discover joy once more. The bonus in this film is a fascinating insight into the slowly changing attitudes of modern Japan toward everything from ballroom dancing to physical contact. There are scenes that will make you laugh out loud ... a few where you\'ll want to get up and tango ... and many others where you\'ll just feel good.<br /><br />This is a great introduction to contemporary Japanese filmmaking for those who might be under the impression that all Japanese movies are "heavy" and inaccessible. <br /><br />', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I\'m a fan of both actors/singers especially Gackt and when I first discover this movie and watch the trailer,I just think this is a silly one.After a long waiting time,I watched it at last and here\'s my comment...<br /><br />I consider everyone knows the storyline and not going to mention about it,instead of it my first applause goes to acting,generally that Japanese movies hasn\'t got brilliant and acting.Yet in MoonChild\'s all cast is simply wonderful and got into it,especially Gackt reflects his characters emotions and changes pretty well,I like many of his scenes both dramatic and humorous ones,as for HYDE part,his acting is good but he deliberately staying in background as an actor,respectively as his character do,throughout the movie.I didn\'t like some cinematography especially lighting and some colors but due to small budget,it still has brilliant moments,but the real jewel of the film is story.It has some cheesy moments but it\'s OK for me,and the friendship theme of the movie is really well developed and touching at sometimes,on the other hand story points out a cruel world which no ones life guaranteed and with some memorable death scenes it reflects this theme to the visuals.An interesting note aside,this movie has some similarities with excellent vampire movie Interwiew with the Vampire which is also played by the most beautiful(not handsome,beautiful)actors of American cinema,actually Moon Child is somehow can be seen as brother with Interwiew,yet original on it\'s own.Only problem that MoonChild is it\'s a bit slow sometimes,I\'m a Japanese movie fan and I used to that but it\'s not change MoonChild has some useless scenes or characters.But all in all;this movie is really good and very emotional sometimes,as for actors/singers duo I hope to see their other movies in future,and I recommend this to everyone who likes vampire-action-sci-fiction and romance films 8/10', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I teach Japanese for an online high school and I include cultural activities so that the students can learn about the country as well as the language. And watching "Gung Ho" is one of the requirements. The students can either buy or rent the movie. Stereotypes or not, this helps the students to see that other people view the world and their lives differently than we do. Many of my students have told me that they enjoyed the movie so much, they are going to get a copy for themselves. It is really interesting to see what we value in this culture and what they value in their culture. I just wish I could get a cleaned-up TV version. I\'m not really into the crude language the auto workers use all the time.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I have a 5 minute rule (sometimes I\'ll leave leway for 10). If a movie is not good in the first 5 or 10 minutes it\'s probably not going to ever get better. I have yet to experience any movie that has proved to contest this theory. Dan in Real Life is definitely no exception. I was watching this turkey and thought; wow, this is not funny, not touching, not sad, and I don\'t like any of the characters at all.<br /><br />The story of an advice columnist/widower raising three young daughters, who falls in love with his brothers girlfriend. I suppose the tagline would be "advice columnist who could USE advice"? I don\'t know. Dans character in no way struck me as someone qualified to give advice. I guess THAT\'S the irony? I don\'t know. He goes to see his parents, brothers, sisters and their kids at some sort of anual family retreat, which seems very sweet, and potential fodder for good comedy, story lines...none which ever emerge. The central story is basically how he loves this woman, but can\'t have her. Anyone with a pulse will realise that eventually he WILL get her, but you have to suffer through painfully unfunny, trite, lifetime movie network dialogue "murderer of love" to get to the inevitable happy ending.<br /><br />This is truly one of the worst movies I\'ve ever seen.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('A student filmmaker enlists a B-grade actress (a delectably diva-ish MOLLY RINGWALD!) to complete the horror film that her mother (a dreadfully dull Kylie Minogue!) tried to make 12 years ago. It\'s a curious plot choice to say the least, as any Aussie horror fan knows that the genre is sadly lacking in women directors. The film has a curse on it, because Molly had to kill some psycho murderer on the original set. But she\'s back, because she needs the exposure. Unfortunately, the curse is still there and people start dying on the "set." Cut is an Aussie attempt at the modern "slasher," but unfortunately it doesn\'t bring anything new or exciting to the table. In fact, it rips half of Wes Craven\'s 90s filmography. Lots of film-world name-dropping a la "Scream" (except it\'s Aussie name-dropping--Jane Campion...see how this isn\'t as funny) and lots of "is this real or is this a movie" a la "New Nightmare." The editing is bad, the music is annoying, the effects are laughable, almost everything is bad about this. Fortunately, the film can have a sense of humor: at one point, a well-dressed girl in the movie crew says to the owner of the house they are filming at: "Don\'t worry, we\'ll treat your house as if it were our own," to which he responds, "that doesn\'t mean anything to me, you look like you live in a dump!" Ha! And Molly\'s ridiculous one-liners were enough to not regret renting this one. "You got any diet coke in here?" (as she rides in the film professor\'s car) and "Does anyone know where I can buy any tofu?" (the first thing she mutters on the set) and "Where the hell is my agent?" (oh wait, that\'s what I was thinking for her.)', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I know that movies aren\'t necessarily supposed to mirror reality, but this one got on my nerves. It perpetuates ignorant stereotypes about "psychological trauma" and mental illness. The "psycho mom" thing has been done too many times before (and usually done better) and much of the rest of the plot is far-fetched as well. The acting was not horrible but nothing to rave about.<br /><br />One highlight: I am a long-time fan of General Hospital and it was a trip to see one of the roles played by former GH regular, Jon Lindstrom.<br /><br />Anyway, if you can overlook the bogus psychoanalytical part of it, in the same way a person must suspend reality / judgment when watching a lot of movies, then this movie might be tolerable. If you have nothing better to do and fairly low standards.<br /><br />I\'m sorry I spent my time watching it.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('There can be no denying that Hak Se Wui (Election in English) is a well made and well thought out film. The film uses numerous clever pieces of identification all the time playing with modernity yet sticking to tradition  a theme played with throughout the film Where John Woo\'s Hong Kong films are action packed and over the top in their explosive content as seen in Hard Boiled (1992) and when Hong Kong films do settle down into rhythms of telling the story from the \'bad\' point of view, they can sometimes stutter and just become merely unmemorable, a good example being City on Fire (1987).<br /><br />Election is a film that is memorable for the sheer fact of its unpredictable scenes, spontaneous action and violence that are done in a realistic and tasteful (if that\'s the right word) manner as well as the clever little \'in pieces\' of film-making. It\'s difficult to spot during the viewing but Election is really constructed in a kind of three act structure: there is the first point of concern involving the actual election and whoever is voted in is voted in  not everyone likes the decision but what the Uncles say, goes. The second act is the retrieving of the ancient baton from China that tradition demands must be present during the inauguration with the final third the aftermath of the inauguration and certain characters coming up with their own ideas on how the Triads should and could be run. Needless to say; certain events and twists occur during each of the three thirds, some are small and immaterial whereas some are much larger and spectacular.<br /><br />Election does have some faults with the majority coming in the opening third. Trying to kill off time surrounding an election that only takes a few minutes to complete was clearly a hard task for the writers and filmmakers and that shows at numerous points. I got the feeling that a certain scene was just starting to go somewhere before it was interrupted by the police and then everyone gets arrested. This happens a few times: a fight breaks out in a restaurant but the police are there and everyone is arrested; there\'s a secret meeting about the baton between the Triads but the police show up and everyone gets arrested; some other Triads are having a pre-election talk but the police show up and guess what? You know.<br /><br />Once the film gets out of that rut that I thought it would, it uses a sacred baton as a plot device to get everybody moving. The baton spawns some good fight scenes such as the chasing of a truck after it\'s been hotwired, another chase involving a motorbike and a kung-fu fight with a load of melee weapons in a street  the scenes are unpredictable, realistic and violent but like I said, they are in a \'tasteful\' manner. Where Election really soars is its attention to that fine detail. When the Triads are in jail, the bars are covered with wire suggesting they\'re all animals in cages as that\'s how they behave on the outside when in conflict. Another fine piece of attention to detail is the way the Uncles toast using tea and not alcohol, elevating themselves above other head gangsters who\'d use champagne (The Long Good Friday) and also referencing Chinese tradition of drinking tea to celebrate or commemorate.<br /><br />Election is a good film that is structured well enough to enjoy and a film that has fantastic mise-en-scene as you look at what\'s going on. Some of the indoor settings and the clothing as well as the buckets of style that is poured on as the search and chase for the baton intensifies. The inauguration is like another short film entirely and very well integrated into the film; hinting at Chinese tradition in the process. I feel the best scene is the ending scene as it sums it up perfectly: two shifty characters fishing and debating the ruling of the Triads all the while remaining realistic, unpredictable and violent: in a tasteful manner, of course.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('The film is severely awful and is demeaning to rape victims. On the surface, it may be a daring film about rape but if you dig beneath the surface, what lies is a not-so-positive message about rape. Aishwarya the rape victim is shown to be a helpless victim who cannot cope all because she is a WOMAN. She needs a MAN to help her. When the society makes jibes about her and throws comments at her, she does not stand up for herself. It is all left to Anil Kapoor to do all the talking while Aishwarya does all the crying.<br /><br />The director (Satish Kaushik) went down the wrong path by portraying a rape victim as weak and submissive. What would have been more effective is portraying a strong woman who rebels against her enemies in a courageous way. The director is famous for being chauvinistic. His films are usually full of weak women but he tries to hide them in controversial roles. He needs to learn that just because the role is controversial, it does not mean that the character herself is strong.<br /><br />The most degrading scene in the film is when Aishwarya \'cleans\' herself after just being raped. She does it to please her father who thinks that she is now dirty. Though it is commendable that Shah shows the stigma against rape victims in such a stark light, what he does not show us is whether Ash\'s father was wrong for making his daughter do such a thing. Thus we are left with a confusing message about rape.<br /><br />The comedy too is not needed in a strong subject film like this. Even more so, the comedy is simply not funny. Ash is wooden in her role while Anil Kapoor does nothing but shout. The music is mediocre except for the title track, which is beautifully picturised (the only bright point of this film). Sonali Bendre\'s role is disappointing and pointless. Overall, what could have been a great movie to remember ends up being an awful mish-mash that will give some viewers severe indigestion.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This is not horror, as the first part was: This is ("campy") light and humorous entertainment. Like in so many sequels, the action starts right away with no explanations. But there\'s boobs, so I don\'t complain. And real boobs that is. If I understand correctly, those are quite rare today amongst the teenage girls in U.S. of A. Which brings to my mind the fact that the main actress here is Pamela "Bruce\'s sister" Springsteen.<br /><br />This cannot be thought without the first movie, so I compare this to it. Again there is too small clothing (mainly pants) and funny hair, it\'s not hard to tell what decade this film is made in. Again there is really strange characters, this time even more visibly "pathological" ones. Especially the personnel of the camp. It\'s like some mental rehabilitation summer camp. People are older: Most of the actors must be at least 25, but I think they\'re supposed to be 16 or something. Some "methods" used by the Evil Dyke are quite unpleasant. Actually this movie don\'t have much in common with the first part, and this is worse than it in every way.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This is the one in which the diminutive Ruth Gordon plays an Agatha-Christie type of murder mystery author who locks her nephew by marriage into a safe. Gordon believes that he murdered her niece and the young fellow dies of suffocation, while Gordon is traveling back and forth to New York. He manages, however, to leave behind some clues, scratches on a couple of black safe deposit boxes and an improvised and well-hidden note. Columbo enters the case, suspects her at once, and solves the mystery by simply using his supernatural mystical intuitive powers. Oh, and Mariette Hartley is on hand as Gordon\'s secretary and would-be blackmailer. Hartley is, I believe, the grand daughter of the psychologist B. F. Skinner. I\'m not sure her ancestry had anything to do with her attractive belly button, which is on display during a belly dance sequence, but I\'ve always admired Skinner anyway.<br /><br />The murder is well handled. It\'s a good plot, and none of the performers or crew fluff anything. But the outstanding figure here is Ruth Gordon, only a skosh over five feet tall. She was over 80 years old and looked it. There are moments when she almost teeters, but she consistently exudes charm. Her acting is idiosyncratic. You can never be sure when she\'s being serious or when she\'s putting Columbo and the audience on. She\'s given some good lines too. What humor there is comes from Gordon. Columbo doesn\'t have any of his frequent comic moments.<br /><br />All in all, a nice job by everyone concerned.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This inept adaptation of arguably one of Martin Amis\'s weaker novels fails to even draw comparisons with other druggy oeuvres such as Requiem For A Dream or anything penned by Irvine Walsh as it struggles to decide whether it is a slap-stick cartoon or a hyper-realistic hallucination.<br /><br />Boringly directed by William Marsh in over-saturated hues, a group of public school drop-outs converge in a mansion awaiting the appearance of three American friends for a weekend of decadent drug-taking. And that\'s it. Except for the ludicrous sub-plot soon-to-be-the-main-plot nonsense about an extremist cult group who express themselves with the violent killings of the world\'s elite figures, be it political or pampered. Within the first reel you know exactly where this is going.<br /><br />What is a talented actor like Paul Bettany doing in this tiresome, badly written bore? Made prior to his rise to fame and Jennifer Connelly one can be assured that had he been offered this garbage now he\'d have immediately changed agents! Avoid.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Although the actors do a convincing job playing the losers that parade across the screen, the fact that these characters are impossible to identify with had me looking at my watch a mere 20 minutes into the film (and more than once after that). The plot development is disjointed and slow, the verbal diarrhoea of the main character\'s only friend is practically insufferable, the base quality of most of the characters actions and the cavalier way in which they are treating is annoying.<br /><br />It is typical of Ventura Pons to put forth crass psychologically handicapped characters. However, this faux sociological analysis is a big step down from CARICIAS or Caresses, where the characters maltreat and despise each other for well founded reasons that play out during that film. In AMOR IDIOTA we are forced to follow the meanderings of a truly subnormal intelligence as he stalks a severely depressed and detached woman. Supposedly this is due to his own depression but the script doesn\'t support that. I won\'t give away the rest of the story just in case there are any masochists out there Is he cured through his obsession or is the woman shocked out of her own depression through his unwavering attention? Even though I watched the whole thing I wasn\'t made to care even for a moment about either of them.<br /><br />If you can sit through all this prejudice, ignorance, betrayal, BAD dialogue, flimsy philosophy, etc the camera-work was pretty good and seems to be something inspired by the DOGMA group. The makeup also seemed to aim at showing these players in a raw and gritty light as it is the worst I\'ve seen Cayetana Guillen Cuervo in any of her movies (while in person she is actually attractive).<br /><br />I suppose if the idea is that we should be forced to see the lower strata of society so we can be grateful we are not part of it then Pons has achieved his objective. The barrage of nearly identical sex scenes was a proper waste of film (if the actors had been filmed but once in blue green clothing the background behind them could have been changed in the special effects studio for a pittance). True that I heard much of the male audience squirm in their seats during this but an objective viewing proves that was not the real aim of those scenes.<br /><br />Save yourselves and watch something else.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Lily Powers works at a speakeasy until her father dies.She then goes to New York to work at an office building.There she notices that if she wants to get any higher she has to give the men what they want.And what men want is her...well, you know.Alfred E.Green\'s Baby Face (1933) is a movie of high sexual content.For a movie of that era, anyway.This was one of the last Pre-Code films that were made.Barbara Stanwyck gives a very sexy performance as Lily.Other actors of this film include George Brent (Courtland Trenholm), Donald Cook (Ned Stevens), Alphonse Ethier (Adolf Cragg), Henry Kolker (J.P.Carter), Margaret Lindsay (Ann Carter) and Theresa Harris (Chico).The young John Wayne is seen as Jimmy McCoy Jr.This movie deals with a brave topic and it does it good.Baby Face is historically significant movie and therefore good to watch.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I watched the trailer on the DVD after seeing the film, and I think anyone who saw it before watching the film would be very surprised and possibly disappointed. It made much of the fact that the film was "by the director of Cube" and made it look like a horror film, when in fact it is an Absurdist comedy (IMDB\'s spell checker doesn\'t seem to think that Absurdist is a word, but it is), reminiscent of Rosencrantz and Guildernstern are Dead.<br /><br />I love the way the story builds up slowly at first, then gradually escalates. I also enjoy the fact that no explanation is given for what happens in the film. That and the fact that the story plays out mainly in just the one set are the only respects in which this film is similar to Cube. I recommend it.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I didn\'t know it was possible to release a movie this bad. The labeling sounded so promising, but you would think that with a cast of 20, at least one of them would be able to act. My wife left me and went to bed after the first 20 minutes. She made a wise decision.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Basically there\'s a family where a little boy (Jake) thinks there\'s a zombie in his closet & his parents are fighting all the time.<br /><br />This movie is slower than a soap opera... and suddenly, Jake decides to become Rambo and kill the zombie.<br /><br />OK, first of all when you\'re going to make a film you must Decide if its a thriller or a drama! As a drama the movie is watchable. Parents are divorcing & arguing like in real life. And then we have Jake with his closet which totally ruins all the film! I expected to see a BOOGEYMAN similar movie, and instead i watched a drama with some meaningless thriller spots.<br /><br />3 out of 10 just for the well playing parents & descent dialogs. As for the shots with Jake: just ignore them.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Bruce Almighty is the best Jim Carrey work since The Truman Show, and was a pleasant surprise after some of his recent "Hey Hollywood - look how good I can act!" box office disappointments. It\'s great to see Jim recognizing and embracing his strengths. He won\'t get an Academy Award but the film itself will last longer than many of the "awarded films" of the Academy. He is at the top of his form in this most recent film - it\'s like the return of an old friend.<br /><br />Carrey, Freeman, and Aniston all do a great job together - comfortable in their comedy roles, superb comic timing, and obviously having fun together but without the "hey mom - look how funny I am" type of comedy. A real surprise was Steven Carrell as Carrey\'s nemesis (Carrell of The Daily Show fame), who walked away with some the best and funniest scenes of the film. I laughed harder at Carell than anyone else in the past three years.<br /><br />I can foresee the religious nuts in the US will be up-in-arms over the treatment of God, but the bottom line of the film is true to all major theological beliefs - we are masses of protoplasms trying to get through our short lives by exercising our free will. Without Married With Children t o complain about, this will likely become a target of people with misplaced priorities (who know the types - men adorned in gold watches on Sunday morning and late nigh television, selling prayers to God). And, again, about 0.5% of the country will care and 80% of the media will report it.<br /><br />The bottom line: this a purely entertaining film, each audience member laughingly wondering what they would do, and a feel-good feeling at the movie conclusion. A walk down any major street in America has to confirm that God has a tremendous sense of humor. What better comic genius to remind us of that than Jim Carry.<br /><br />Thanks again, Jim -- it\'s GREAT to have you back!!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This is just typical Bruce Willis, action movie schtick. Watch it with some popcorn and your buddies. Rent it, to save money.<br /><br />None of it is realistic. The battles aren\'t realistic. The soldiers aren\'t realistic. The victims aren\'t realistic. And why was Tom Skerritt\'s character talking to Willis from the DECK OF THE CARRIER? What\'s up with that? He can\'t do that from inside the ship?<br /><br />Of course, Bruce W. gets a machete wound. There\'s a bunch of average explosions.<br /><br />If this movie accurately represents the Navy SEALS, then don\'t get stuck in Africa expecting them to come rescue you!<br /><br />The noble attack on the village bothered me the most. "Front row seats to an ethnic cleansing"...as Bruce looks at the slaughter going on in town. So what does he do? He crawls into town on his belly. Yep. How many died while they were putzing around? Oh well...a body count was needed, I guess.<br /><br />And if that one African guy was so important, why didn\'t he get on the chopper with the elderly and children? Can he say "Duh?" <br /><br />Finally, the movie was very dark. Not just in plot, but so much happens at night it was difficult to make out what was going on.<br /><br />Rent it.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Absolutely stunning, warmth for the head and the heart. The kind of movie western movie makers are too rushed, too frenetic to even attempt. My kids watched it, and they loved it too. What real people--goes to show you how cultural differences (the Japanese setting) is less important than the human similarities. Go see it, whether you like dancing or not.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This movie features a gorgeous brunette named Danielle Petty. She has stunning green eyes, and is in the first few scenes and the last scene. She is the only thing about this movie that is not repulsive. She may not have a future as an actress, because this kind of movie is the kind of offensive disaster that kills careers.<br /><br />The movie itself has absolutely nothing to recommend it. It is not a good horror film, or a good fake journalistic report, or remotely well done. There is no skill apparent in it\'s production. It is like a bad student film. The story\'s horrific elements do not make you sick, it is the fact that it is so poorly done that makes you sick. I would give this movie ZERO stars if I could.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Although I bought the DVD when it first came out, and have watched it several times, I never wrote a review.<br /><br />I loved it when I first saw it and I love it still.<br /><br />Sadly, it seems it never made enough money to motivate anyone to do a follow-up. I have to assume QT still controls the rights, but after Kill Bill if he does a film that is as true to the comics and books as My Name is Modesty, with another tough female lead, anyone not familiar with the character will see this as a let-down.<br /><br />Peter O\'Donnell wrote his stories to focus more on psychological suspense rather than action thrillers.<br /><br />The tug of wills between Modesty and Miklos is very true to the source material and is tense, suspenseful and fascinating to anyone who doesn\'t have to have gore and explosions. Alexandra did a great job in playing how O\'Donnell\'s character would have taken control of the situation.<br /><br />I find this particularly ahead of the curve following the sorely needed reboots of Batman and James Bond. After 2 dismal earlier efforts, although not nearly as well known to the public, this is really a reboot of the Modesty character, and it is really sad that probably no more films about her will be made.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Ulises is a literature teacher that arrives to a coastal town. There, he will fell in love to Martina, the most beautiful girl in town. They will start a torrid romance which will end in the tragic death of Ulises at the sea. Some years later, Martina has married to Sierra, the richest man in town and lives a quiet happy live surrounded by money. One day, the apparition of Ulises will make her passion to rise up and act without thinking the consequences. The plot is quite absurd and none of the actors plays a decent part. IN addition, three quarters of the film are sexual acts, which, still being well filmed, are quite tiring, as we want to see More development of the story. It is just a bad Bigas Luna\'s film, with lots of sex, no argument and stupid characters everywhere.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('A charming, funny film that gets a solid grade all around. I saw a screener of this film recently at work. It was so nice to see this film in contrast with all the crappy horror movies I see every day. So much so, that I figured I\'d write in. Not sure if this film is going to theaters, but I hope it does. Its a nice film to see with friends, its a charmer, and has some funny jokes. The acting was terrific (especially Howard Hessman and Larry Dorf. The directing was pretty good (not a film that needed to be over-directed). What really makes this film stand out I think is the writing. It was like Neil Simon, Seinfeldish, and the banter between characters is smart and has a nice rhythm. As an aspiring screenwriter, I notice those things! (I\'m a dork). Anyway, a really cute film that I recommend.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('First of all, I\'d like to tell you that I\'m into comics, anime, animation and such stuff. It is true that everyone has his own preferences, but you can trust me on this movie. I\'ll be objective. To begin with the story - it\'s OK. Follows the story line of the comic books as far as I\'m familiar with them. But the animation... Well, it\'s not actually terrible, but it\'s definitely cheap and mediocre. It would be a lot better if they didn\'t try to imitate the anime style and sticked to the original comic book style drawings. If we pretend not to see the rare sloppy effects like fire and lightnings you could tell that the movie is made about 10 years ago and even more. Looks a little bit like the original Vampire Hunter D from 1985. Take a look at Heavy Metal FAKK 2000 for instance - 4 years ago they made a movie that looks a hell lot better! In addition to this the voice talents do nothing remarkable, the music is nothing special. So all in all - it lacks atmosphere. I watched it, but I cannot tell I really enjoyed it. It just does not capture you. There\'s plenty of blood and violence, but that does not impress me at all. May be it will be shocking for someone who was never watched more mature oriented animations and sees animated blood for the first time (is there anyone around?), but I don\'t think this is the audience for this movie. So they could add a little nudity and spice to it. The chicks around Lucifer were quite tasty, and hell, we have Lady Death herself! There are few sexy looks, but that\'s not enough. Instead of Bill Brown\'s music I think it would look better on a hard rock / heavy metal soundtrack. All in all - the movie isn\'t that bad, but if you want something better take the original Heavy Metal, Heavy Metal FAKK 2000, Ralph Bakshi\'s Fire and Ice or Wizards maybe. And of course - Vampire Hunter D: Bloodlust', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This is one of the worst films I\'ve seen. The only positive thing I can say is it was so bad that is seemed comical. First off, there\'s no plot. The actors appear to be reading off cue cards and do the dumbest things. Such as being chased by dead people but yet wanting to go out and look for their friends. Also the zombies were terrible, no where near as fun as any of Romero\'s work, who gets s plug in the movie. And the dumbest part of all was they kept showing flashes of the video game in the action sequences. Like we don\'t get the video game is about shooting zombies. Also, all the 20 somethings some how know how to use automatic weapons and hit a target without even aiming the gun. And the way the people die is so stupid. It\'s like they run out of ammo so stand around waiting to be jumped on. And when cornered in front of the house they run out of ammo instead of shooting the door open, So dumb.<br /><br />FINAL VERDICT: If any of these actors appear in another film, then they\'ve been blessed with a second chance. Definitely the worst film I\'ve seen in years. A B-movie on cinemax is better.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie was like "The Disney Channel after Dark." Take out the "aren\'t we naughty" language and themes and you are left with dialogue and plot devices that insult the intelligence of anyone who doesn\'t describe "Saved by the Bell" as quality television. The dialogue so laughably cliched and knowingly dirty, one might think the screenplay was the product of locking Aaron Spelling and Joe Eszterhas in a room with orders to produce an amalgam of every bad script each had ever had a hand in creating. If that was Roger Kumble\'s intention, mission accomplished.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('God I love this movie. If you grew up in the 80\'s and love Heavy Metal, this is the Movie for you. They really don\'t get much better than this. The Fastway soundtrack is one of the best soundtracks ever. I put on the record when it first came out and spent the next month learning every song on guitar note for note. The plot outline is your standard Heavy Metal horror movie. Kid\'s favorite singer dies. Kid plays record backwards. Hero comes back in demonic form and rocks the town. What more could you ask for?<br /><br />If you haven\'t seen it yet, rush out and buy it. You will not be disappointed. Metal Rules...', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('when i read other comment,i decided to watch this movie...<br /><br />First, cast specially Michael Madsen and Tamer Karadagli; good enough...<br /><br />Film,very intelligence and interesting because ,cast have a lot of international specially European actor and actress like from Turkey and Russsia...<br /><br />Second,Story is basic and you can guess but if you interesting action good play you\'ll like in my opinion...<br /><br />Third,Final chapter is not special or interesting,it\'s regular like other action movies...<br /><br />Finally,i recommend to watch this movie...And i hope You\'ll love it enjoy :D', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This show is beautifully done. When it first came out I though it nothing more than a light-hearted family comedy with quite a few good one-liners. It seemed to express many families really well too, with different concepts of both parent and child, however, like I said, I never thought any more of it then a good watch on an evening. However, my view was shot out the other window when the tragic death of the fantastically funny John Ritter accrued. The programme stood it\'s ground and really commended the characters life in a very sensitive way that also touched the hearts of all the admire res of John Ritter, a fantastic actor with the talent to do anything. When the show aired after Ritters passing, I really wanted to just give my dad a hug and let him know how much he meant to me. I thought this shone threw the acting talents of the three children, particularly that of Bridget\'s character, who was worried of the last words she said to him. It reminded me that no matter what horrible things I say to my dad, I don\'t mean them and it\'s very important that he knows this. Great Show', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I entered the theatre intending to pass a pleasant 90 minutes being entertained if not enlightened. I left neither entertained nor enlightened. This movie can\'t make up its mind what it wants to be and ends up being not much of anything. There are a few funny lines and a few incredibly pretentious movie references (The 400 Blows--for this character? come off it!). While none of the characters gets treated with much respect, the over thirty gay men get the worst of it: all predatory, fat, sad, slobs. If you\'re in the mood for a movie dealing with gay relationships check out Parting Glances, Longtime Companion, Trick, All Over the Guy, Red Dirt, Maurice, Philadelphia instead. You\'ll thank me.<br /><br />', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Watch On The Rhine started as a Broadway play by Lillian Hellman who wrote the film and saw it open on Broadway at a time when the Soviet Union was still bound to Nazi Germany by that infamous non-aggression pact signed in August of 1939. So much for the fact that Hellman was merely echoing the Communist party line, the line didn\'t change until a couple of months later. Lillian was actually months ahead of her time with this work.<br /><br />The play Watch On The Rhine ran from April 1941 to February 1942 for 378 performances and five players came over from Broadway to repeat their roles Frank Wilson as the butler, Eric Roberts as the youngest son, Lucile Watson as the family matriarch and most importantly villain George Coulouris and Paul Lukas.<br /><br />Lukas pulled an award hat trick in 1943 winning an Oscar, a Golden Globe, and the New York Film Critics for Best Actor. Probably if the Tony Awards had been in existence then he would have won that as well. The Oscar is even more remarkable when you consider who he was up against, Humphrey Bogart for Casablanca, Gary Cooper in For Whom The Bell Tolls, Mickey Rooney in The Human Comedy, and Walter Pidgeon for Madame Curie. Every one of his competitors was a bigger box office movie name than he was. Lukas\'s nomination is usually the kind the Academy gives to round out a field.<br /><br />Jack Warner knew that which is why Mady Christians did not repeat her Broadway part and the role of Lukas\'s wife was given to Bette Davis. Davis took the part not because this was an especially showy role for her, but because she believed in the picture and just wanted to be associated with it. It\'s the same reason she did The Man Who Came To Dinner, a much lighter play than this one.<br /><br />Davis is the daughter of a late American Supreme Court Justice who married a German national back in the Weimar days. After many years of being vagabonds on the continent of Europe, Davis Lukas, and their three children come to America which has not yet entered the European War. They\'re made welcome by Lucile Watson who is thrilled naturally at finally meeting her grandchildren.<br /><br />The fly in this ointment are some other house guests, a friend of Davis\'s from bygone days Geraldine Fitzgerald and her husband who is also from Europe, a Rumanian diplomat and aristocrat George Coulouris. Coulouris is a wastrel and a spendthrift and he smells an opportunity for double dealing when he suspects Lukas\'s anti-fascist background. <br /><br />His suspicions are quite correct, it\'s the reason that the family has been the vagabonds they\'ve become. Lukas fought in Spain on the Republican side and was wounded there. His health has not been the same since. His family loyally supports him in whatever decision he makes. Those decisions affect all the other members of the cast.<br /><br />Adding quite a bit more to the Broadway play including some lovely fascist creatures was Dashiell Hammett who was Lillian Hellman\'s significant other. Coulouris playing cards at the German embassy was a Hammett creation with such loathsome types as Henry Daniell, Kurt Katch, Clyde Fillmore, Erwin Kalser and Rudolph Anders.<br /><br />Coulouris is truly one of the most despicable characters ever brought to screen as the no account Runmanian count. He was a metaphor for his own country who embraced the Nazis with gusto and then equally repudiated them without losing a step after Stalingrad.<br /><br />Lucile Watson was up for Best Supporting Actress in 1943, but lost to Katina Paxinou in For Whom The Bell Tolls. Dashiell Hammett was nominated for best adapted screenplay and the film itself lost for Best Picture to that other anti-fascist classic, Casablanca. <br /><br />Though it\'s an item firmly planted in those specific times, Watch On The Rhine still packs a stern anti-fascist message that bears repeating infinitely.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I always have a bit of distrust before watching the British period films because I usually find on them insipid and boring screenplays (such as the ones of, for example, Vanity Fair or The Other Boleyn Girl), but with a magnificent production design, European landscapes and those thick British accents which make the movies to suggest artistic value which they do not really have.Fortunately, the excellent film The Young Victoria does not fall on that situation, and it deserves an enthusiastic recommendation because of its fascinating story, the excellent performances from Emily Blunt, Paul Bettany and Jim Broadbent, and the costumes and locations which unexpectedly make the movie pretty rich to the view.And I say "unexpectedly" because I usually do not pay too much attention to those details.<br /><br />"Victorian era" was (in my humble opinion) one of the key points in contemporary civilization, and not only on the social aspect, but also in the scientific, artistic and cultural ones.But I honestly did not know about the origins from that era very much, and maybe because of that I enjoyed this simplification of the political and economic events which prepared the landing of modern era so much.I also liked the way in which Queen Victoria is portrayed, which is as a young and intelligent monarch whose decisions were not always good, but they were at least inspired by good intentions.I also found the depiction of the romance between Victoria and Prince Albert very interesting because it is equally interested in the combination of intellects as well as in the emotions it evokes.The only fail I found on this movie is that screenwriter Julian Fellowes used some clichés of the romantic cinema on the love story, something which feels a bit out of place on his screenplay.<br /><br />I liked The Young Victoria very much, and I really took a very nice surprise with it.I hope more period films follow the example of this movie: the costumes and the landscapes should work as the support of an interesting story, and not as the replacement of it.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('It is a tricky thing to play a queen. On the one hand, the actress has to be majestic and imperious, and on the other, she has to show vulnerability in a tough situation as well as the gathering of the courage and resolution to overcome the odds, since almost all movies about queens have that basic plot line. <br /><br />Emily Blunt is quite radiant as Victoria, but it\'s not as full a performance as I\'d like, no blame to her. I can\'t help but feel like this is a Mills & Boon novel adaptation compared to a darker, more dramatic movie about another young queen, Elizabeth. Hence Blunt doesn\'t get to run the gamut of queenly emotions, at least not to the full extent, since she\'s, y\'know, the young Victoria. To see the old Victoria, check out Mrs Brown.<br /><br />Jean-Marc Vallee is an interesting choice of director for the movie. He last did C.R.A.Z.Y., which was excellent and propelled him to fame. It was quite a different movie but I remember it looking gorgeous and that\'s probably the main similarity between the two movies. But while Vallee wrote C.R.A.Z.Y., this one was by Julian Fellowes, and though I really enjoyed his Gosford Park, the story for this movie was much less interesting. I soon got lost with all the governmental politics. Maybe it was less engaging because there was no potential beheading of the monarchy. I\'m just saying.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I happened to see this movie twice or more and found it well made! WWII had freshly ended and the so-called "Cold War" was about to begin. This movie could, therefore, be defined as one of the best "propaganda", patriotic movies preparing Americans and, secondly, people from the still to be formed "Western NATO block" of countries to face the next coming menace. The movie celebrates the might of the US, through the centuries, while projecting itself onwards to the then present war, which had just ended. Nice and funny is the way of describing the discovering of the American Continent by Columbus and pretty the "espisode" of New Amsterdam and the purchasing of Manhattan from a drunk local Indian .. Must see it (at least once, for curiosity of fashion of propaganda through time)! :)', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I began riding horses fairly recently, and, as anyone who has ever ridden should know, I fell in love with horses and their world. I rented Spirit on a whim, just trying to pack my life full of as much horse related material as I could, and I was surprised by the results.<br /><br />What I expected was a feel-good Disneyesque movie with talking animals and stereotypes every five minutes.<br /><br />What I got was an amazing film, filled with beautiful scenery and animation, and an amazing storyline that has the great potential to warm one\'s heart.<br /><br />Spirit is a wild mustang in the Old West, whose entire world is brought crumbling down around him when he discovers the humans slowly taking over his homeland. The story unfolds with a wide array of characters, some human, some animals, all are well written and most are pleasant to watch on screen.<br /><br />I would recommend this movie to anyone who enjoys a good story, and who has an appreciation for history and animals.<br /><br />One thing I forgot to mention, but that I feel is important, is that the animals in this film do not talk. This was a really nice vacation from the Lady And The Tramp animated movies that everyone today is used to.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('The TV guide described the plot of SEVERED TIES as thus : " An experiment on a severed arm goes awry " so right away I thought this was going to be about an arm that`s got a mind of its own as seen in THE BEAST WITH FIVE FINGERS or THE HAND or someone getting an arm transplant as in BODY PARTS . Both premises are tried and tested , or to be more accurate tired and tested so I was curious as to how the producers would approach the story . I actually thought they were making an arthouse movie like PI down to the use of B&W photography at the start of the film but the makers seemed to have tired of this approach after 20 seconds and decided to make a splatter comedy similar to THE EVIL DEAD . I`ve very little to say on this except that I disliked THE EVIL DEAD movies and I disliked SEVERED TIES and it seems really unfair that films like this use an obscene amount of rubber when the third world is crying out for condoms', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('When this movie first came out back in 1984, Prince was one of the hottest acts around. Everyone wanted to see this movie, which was not much more than a extended music video. The acting was pretty bad, but what can you expect from musicians acting on the big screen for the first time? Despite that, it was still a very entertaining film! Morris Day and Jerome Benton provide some all time classic comedy, especially their rendition of "The Password", which will make you think of Abbott & Costello doing their "who\'s on first" baseball routine.<br /><br />Appolina (who went by a single name then) provided some beautiful breasts, so you had the brief nudity covered. Plus, she is very attractive. And of course, the soundtrack of the album is one of the best Prince ever recorded. Prince later on had a fallout with Warner Bros. and changed his name, but at this particular time in his career, he was at the top of his game.<br /><br />This movie doesn\'t rank in the all time great category, but it is pretty entertaining.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I could only get through about 25 mins of it. Not one laugh in the 25 minutes I gave it, one of the most painful films I\'ve ever had to endure. Chris Kattan is so nervous on screen that it made me nervous to watch him. Just a horrible movie.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('For two of the funniest comedians, the movie was awful. Fast forwarded it and never got any better! Waste of time and waste of money! Tina Fey is such a great writer, I thought that she would be so great in the comedy. The previews were so great, but they only showed the best parts of the movie. My husband even thought that for a chick flick, it sucked. What is up with that. Movie was very slow ans boring. I will not recommend it to anyone at this time. I would like my money back for this one! BOO from us here in Arizona. Thanks but no thanks. Who does this kind of stupid stuff to make people think that you are pregnant. I thought that it was going to be so funny, I have had my own children and I have helped others have children. It could have been more along the lines of reality.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Terry West had a good idea w\ this movie. He just didn\'t flesh it thru. There are endless shots of the creepy looking school\'s exteriors that go on forever and probably to pad the film\'s running time. Also at this school there are only 2 students. Misty Mundae is good as usual but this film will always belong to Ruby LaRocca (which is the only reason to watch the film in the beginning). If the script centered on her interesting character we\'d have a movie to watch. She is so GORGEOUS!! Good news for DVD buyers, Terry West\'s earlier (and better) film "Blood For The Muse" is a special feature. One thing I\'d like to say is that this movie feels like someone who\'s not good at delivering the punch line at the end of a long joke for the ending feels that very same way. Then again, just watch this for Ruby LaRocca.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie is really nothing besides an admittedly well-crafted series of tense sequences punctuated with an inevitable "gotcha!" at the end of each. Really, there is no character development and no real plot to speak of. There are only the most skeletal of motivations for the characters to do anything while they trudge forward to their unavoidable dooms. It\'s all just an excuse to show a creepy ghost kid (who seems to have gotten some of the family cat mixed up in his ectoplasm) and his ghost mom (with long black hair hanging in her face kind of like "The Ring") take down a bunch of cardboard cut-out, two-dimensional excuses for human characters.<br /><br />This English-language version of "The Grudge" is the equivalent of cinematic junk food; satisfying momentarily, but not really what you ought to be living on.<br /><br />Not recommended.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I think I read this someplace: Joe Johnston (director of the film and also one of the guys who founded Industrial Light and Magic for work on the first Star Wars film) and one of his producers or something were racking their brains for a title for the movie, "Rocket Boys" (I guess) was lacking something.<br /><br />One day they were messing with a PC program that forms words from other words (ie: you type in a word or series of words and it mixes the letters up and forms other words) I think the technical term is an "anagram"<br /><br />Anyway, they typed in "Rocket Boys" and sure enough what comes back is "October Sky". They were shocked to say the least. The title summed up everything in the movie since the movie revolves around Sputnik. At first Homer Jr did not like the idea, but he warmed up to it after the "movie poster paperback novel" came out and took off.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Kenny Doughty as Jed Willis is sexier in this role than any male porn star, even though he keeps his pants on.<br /><br />The movie tore at my heart reminding me of the intensity of the big explosive love of my life. I don\'t think I can think of another movie, except perhaps Zeffirelli\'s Romeo and Juliet that captures that giddy joy that well.<br /><br />The other draw of the movie is the very English eccentric characters enjoying the scandal vicariously. In that sense it is much the same appeal as Midsomer Murder or a Miss Marple mystery, without the mayhem.<br /><br />This is a great antidote to the mock horror currently popular in the USA an any relationships between people of different ages.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('It seems that the people behind Envy realised that recent comedies - especially ones involving Ben Stiller and to a lesser degree Jack Black - have been situation spoofs, which have steadily declined in originality and generally laughs. I found the sheer absurdity of Zoolander utterly hilarious when it was released, Starsky and Hutch was also enjoyable, and then Dodgeball kept the laughs going for a lot of people, although personally i was a bit tired of the over-the-top characters - especially when the scenario wasn\'t quite so funny (perhaps the comedy of a Dodgeball tournament doesn\'t quite translate to Australia, where it\'s rarely played). So in an attempt to do something a little more original, Envy moves away from an absurd scenario and instead revolves around the absurd creation of Jack Black\'s character (i won\'t spoil what it is for those who intend to see the movie). The problem is that the movie seems to drag, i\'m not a big enough movie buff to be able to think of examples, but it seems like this set up has been done a thousand times before - and very rarely successfully. So instead of a nice, crisp, enjoyable and fresh comedy, you get a film that seems to just go through the motions. Sure the motions can be quite amusing, and they\'re centred on an idea that is quirky enough to provide a few laughs - especially with Jack Black playing the excited and amusing, though a bit 2D, creator. Ben Stiller on the other hand seems a bit lost, he\'s asked to play a fuller role than the ridiculous characters of his Zoolander breed of movies, but he struggles as a family man, whether his fault or the scripts, there isn\'t enough depth to the character and the result is a movie of Ben Stiller doing those typical mannerisms and generally becoming tedious. The performance doesn\'t leave an imprint on the viewer (he\'s just Ben Stiller, Jack Black manages to actually portray a character - though not a challenging one). The last annoying element of the movie is Christopher Walken\'s role as \'The J Man\', which is about as typical and two dimensional as characters come, and naturally he becomes monotonous and frustrating very quickly.<br /><br />It\'s really not as unbearable as some people would have you think, it\'s watchable, especially if you\'re in the right mood (feeling silly would be a good prerequisite for seeing this film). Hire it on a movie night with friends and watch it after you\'ve watched a scary film and feel like something light - hopefully you\'ll also be somewhat tipsy by then too. In that scenario i can imagine it would be quite enjoyable, but generally it provides too few laughs to carry itself and most of the time just drags along.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I mean really, how could Charles Band the head of Full Moon let a total stink-ball like DEMONICUS out. I mean it should never got the green light to begin with. The story is repetitive, the characters are weak at best, there is no real story on Tyranus other then he\'s a bad dude. Then they writer or director goes out his way for a bad ending. That\'s right a bad ending, Demonicus rises. The last survivor escapes a deadly cave in, then a picture of Chimera comes to life, cheaply I might add and chases her out. Then as she is walking home ala FUNHOUSE. A statue that has been destroyed centuries ago reappears for no reason just to collapse on top of her. I mean, that makes no sense. What the hell was Charles thinking allowing this pile of puke to be made, with four different movie companies they were that desperate for movies. They could have asked me, I had better ideas then DEMONICUS. THANKSGIVING TURKEY.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This was a crappy movie, with a whole lotta non-sense and too many loose-ends to count. I only watched this movie because one of my favorite actors (Ron Livingston) made a cameo in it, and I continued watching it because as a girl, I love any movie that includes male nudity for a change. Later, I found myself wondering just how much more ridiculous the storyline could get, and each time it got...more... ridiculous.<br /><br />Sean Crawley (good-looking Chris L. McKenna, whom I\'ve never seen before - but LOVED his little nude scene)is making ends meet as a painter, when he meets electrician Duke Wayne (George Wendt from "Cheers"). Thinking he\'s getting more work from Duke, Sean agrees to meet contractor Ray Matthews (Daniel Baldwin, playing a stereotypically evil guy). Ray is being investigated by a City Hall accountant (Ron Livingston in a cameo, who I\'ve been in love with from "Office Space" up to "Sex & the City"). Ray end up offering the apparently desperate-for- cash Sean $13k to kill the accountant, and Sean accepts the job. Sean stalks out the accountant, whose wife (Kari Wuhrer) he finds himself attracted to, completes the hit, and leaves - taking the file of information against Ray with him. Sean quickly learns he was being used, that Ray never intended to pay him, and Sean uses the file as leverage to get his money.<br /><br />Up to this point, it\'s a descent flick...generally worth watching. But as soon as Ray, Duke and their crew kidnap Sean to muscle the information about the file out of him, it just got dumber and dumber (and still DUMBER...), until finally it seemed like the film\'s writer, Charlie Higson, had snapped out of a 10-day writing hangover and realized he needed to desperately figure out how to wrap up the series of implausible messes he created before a deadline or something. Without simply detailing the movie, let\'s just say that in every-single-scene you watch after the kidnapping, you find yourself gasping "what the f**K!," baffled by the ongoing nonsense as Sean follows a fairly graphic and gross path towards redemption. In the end, so many loose-ends are left in the movie, that you begin to regret that you even watched it.<br /><br />This is a movie that you should only watch after it hits cable, and you should have enough beer and friends around to mock the film to it\'s full value. It\'s supposed to be a psychological thriller, and McKenna is a decent actor, but it\'s hard to give yourself to the movie when you have "Norm" from "Cheers" and a Baldwin brother doing the dirty work, and a kidnapping strategy that really makes no damned sense. Guys will love the violence, blood and guts scenes, and the absolutely unnecessary sex scenes and boob shots. Girls will enjoy handsome Sean\'s gratuitous crotch shot in a mainstream movie, when its almost always the girls that get stripped down in a movie. Personally, I hate that the only actor worth watching for more than his looks (Ron Livingston) is only in the first one-third of the movie.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I first saw this movie as a pre-teen, about the age when kids start to think through their identity. I was greatly affected by the scene of the man and the children who he raises as his own. The eldest boy has been taunted that his mother is a prostitute and none of his siblings have the same biological father (which Kurosawa makes obvious by having children who look nothing like each other). The man still persuades tho boy that he is their father by the only definition that counts. The man is acclaimed to be father by all of the children but one, who still prefers her brother.<br /><br />Each of the vignettes are likewise compelling for their own stories and conclusions.<br /><br />It\'s a great film, even if it is not the greatest Kurosawa film.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I saw this movie the other night. I can\'t even begin to express how much this movie sucked. The writing, the voice acting, even the claymation. Terrible, Terrible, Terrible. It\'s like watching 24 hours of C-Span for the sake of comedy. It just doesn\'t work. It literally falls flat at about every spot possible.<br /><br />Also, the movie\'s animation is very poor quality. I know that this is an movie made by one person, but to think that he could make 97 minutes worth of crap, maybe he could at least make 1 second worth of funny.<br /><br />This show may take the cake for being the worst film of all time. Yikes. It really was that bad. If you\'re looking for a movie that will make you laugh, steer clear from this abomination. My advice: Don\'t even buy it, or look it up for that matter. Your brain will than you.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I cannot believe that I wasted five hours of my life on this rubbish. The previous five day offering by this author was highly enjoyable and I was really looking forward to this. But most of the dialogue was completely incomprehensible. Suranne Jones was the principal culprit since she either mumbled or gabbled her lines, but most of the rest of the cast followed her example. Notable exceptions were Bernard Hill and Anne Reid, old stagers whose diction was exemplary. Do producers not listen to productions before they are aired to make sure the dialogue is audible? As a result I suppose I lost track of what was going on, and since the original plot line seemed to metamorphose into to the standard them-and-us thing between Muslims and the rest I soon lost interest. The ending was a complete anti-climax. A complete dud.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('"Dance, Fools, Dance" is an early Crawford-Gable vehicle from 1931. Crawford plays a Bonnie Jordan, a wealthy young woman whose life consists of parties, booze, and stripping off her clothes to jump from a yacht and go swimming. This all ends when her father dies and leaves her and her brother (William Blakewell) penniless. Bonnie gets a job on a newspaper using the name Mary Smith; her brother goes to work for bootleggers. The head man is Jake Luva - portrayed by Clark Gable as he plays yet another crook. Later, of course, he would turn into a romantic hero, but in the early \'30s, MGM used him as a bad guy. Not realizing that her brother is involved in illegal activity, Bonnie cozies up to Luva.<br /><br />Gable and Crawford made a great team. Her facial expressions are a little on the wild side, but that, along with her dancing, is one of the things that makes the movie fun. Look for Cliff Edwards, the voice of Jiminy Cricket, as Bert.<br /><br />It\'s always interesting to see the precode movies, and "Dance, Fools, Dance" is no exception.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Okay, during this past thanksgiving break, whilst having the whole family together everybody decided to go see a movie, and since Fred clause was voted majority, thats what we went and say. <br /><br />To start off the movie had so many plot holes it was pathetic. Simple explanations of why a certain event was happening was void. example; who the heck is trying to \'shut down\' Santa clause? Is it some sort of corporation? A little explanation would of been lovely. <br /><br />Second: The movie tossed you flimsy characters that evoked no sympathy from you about their feelings or actions. example: the little elf named Willie and the only tall girl in the elf village. they see each other twice and then they are a couple and i could of cared less because this movie didn\'t make me care. <br /><br />Third: I suppose this was suppose to be a family film? Its rating was low at just PG. For a family film there were several articles of suggestive conversation. It didn\'t bother me, but if i were a parent i could see a problem. <br /><br />Through the whole movie Paul Giamatti looked extremely bored with his role, but honestly he was the only one worth watching in the movie. Vaughn had a few funny moments but played the same character he has for the last two movies. mouthy frat boy. (nothing against Vaughn, he\'s been good in other movies)<br /><br />so this movie gets a 3 out of 10 stars from me, just because somebody had to put in the effort to produce, film and release this flick. <br /><br />In my opinion i would definitely pass on this flick, or if you HAVE to see it save it for a rainy day rental.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I have wanted to see this for the longest time, James Merendino is a great director. SLC Punk is one of my favorite movies, and in the first ten minutes of this film I thought that it was a great follow up after that though, it begins to drag. The acting and direction were terrific. In fact everything in the film seemed to flow except for the script. At times, the only thing keeping my attention was the fact that in the cast was the most beautiful woman in the world, Claire Forlani. This film was good, but I expected more.<br /><br />P.S. Look for great cameos by Chi McBride, and Chris McDonald.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Writer/Director John Hughes covered all bases (as usual) with this bitter-sweet "Sunday Afternoon" family movie. "Curly Sue" is a sweet, precocious orphan, cared for from infancy by "Bill". The pair live off their wits as they travel the great US of A. Fate matches them with a "very pretty" yuppie lawyer, and the rest is predictable.<br /><br />Kids will love this film, as they can relate to the heroine, played by 9 year old Alisan Poter (who went on to be the "you go girl!" of Pepsi commercials). The character is supposed to be about 6 or 7, as she is urged to think about going to school. Some of her vocabulary suggests that she is every day of 9 or older.<br /><br />Similar to "Home Alone", there is plenty of slap-stick and little fists punching big fat chins. Again, this is "formula" film making, aimed at a young audience. Entertaining and heartwarming. Don\'t look for any surprises, but be prepared to shed a tear or two.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I first saw a track from this DVD at a hifi show Nov 2006 in London ( i was not really into cream until now!!).It was through a high end Arcam system,it sounded great with dts.I had to get this DVD and i\'ll tell you this is by far the most exciting music DVD i have ever watched.The performance of Cream at their age was just mind blowing and sound quality is the best i have heard on a music DVD.It does not matter what type of music you like,this one will definitely grow on you.It\'s the sheer brilliance of their performance that will make you watch it again and again.Even new musicians don\'t cut the mustard these days, as these old rockers do.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Up until the sixth and last episode of the Star Wars saga, which finally ended in 2005, I had always looked at this 1983 entry as my favorite film of the long-running series. The varied action scenes and really different characters (Jabba The Hut, furry woodland creatures, etc.) made this a particularly appealing movie.<br /><br />None of the action ever focused too long in one spot, either. The last half hour exemplifies this the most as the scene switches every few minutes from the woods to the battle among space ships to the individual laser-duel between Luke Skywalker and Darth Vader.<br /><br />Another nice characteristic this film had that the two previous did not was the absence of in-fighting between two of the stars. Gone was the incessant bickering between Carrie Fisher and Harrison Ford. Finally, everyone was on the same page! It was nice to see.<br /><br />In the end, this was simply a wonderful adventure tale, more than anything else.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I loved this movie for two reasons: 1) Jeff Combs is absolutely wonderful in it. Plays the role of the modern wizard to the hilt. (And is absolutely adorable.) 2) The movie helped to inspire a role-playing game I thoroughly enjoy, Mage: The Awakening. I\'ve shown it at various LARP after-parties, and it\'s always a big hit.<br /><br />D&D love and Jeff-squeeing aside, it\'s not exactly a masterpiece, but it\'s well-done and thoroughly enjoyable. The plot is fast-moving and engaging in its simplicity, the special effects are pretty good for such a low budget, and the script, while nothing stellar, was not too badly done, and cheesy in all the right places. A good way to spend an evening.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('"A wrong-doer is often a man that has left something undone, not always he that has done something."--Emperor Marcus Aurelius <br /><br />The DVD release of "Watch on the Rhine" could not come at a better moment. It restores to us a major Lillian Hellman play stirringly adapted to the screen by Dashiell Hammett (Hellman scholar Bernard F. Dick\'s audio commentary affirms his authorship). It presents a subtle performance by Bette Davis, who took a subdued secondary role long after she\'d become the workhorse queen at the Warner Bros. lot. Equally significantly, it reminds us that World War II had a purpose.<br /><br />Sure, you say, like we needed that. We\'ve heard Cary Grant sermonizing in "Destination Tokyo" (1943) about Japanese boys and their Bushido knives. We\'ve watched jackboots stomp the living hills in "The Sound of Music" (1965). We\'ve toured an England callously occupied by Germany in "It Happened Here" (1966). Yet, truth to tell, we still need the message spread.<br /><br />I have an 81-year-old friend who curses Franklin Roosevelt regularly. He feels that FDR connived the U.S. into a foreign fight we didn\'t need, and thereby caused the death of his favorite cousin. He\'s encouraged in his demonizing of Allied leaders and the trivializing of War Two by Patrick Buchanan.<br /><br />The political columnist has freshly released a fat book heavy with detailed research which claims that Adolf Hitler would have posed no further menace to Poland, Europe, or the world if only the Third Reich had been handed the Free City of Danzig in 1939. Buchanan holds that if those selfish Poles hadn\'t confronted the Nazis, drawing in foolishly meddling Britain and giddily altruistic France, no war would have engulfed the West. He believes that without the rigors of Total War, no one in Germany would have built gas chambers to provide a Final Solution to the Jewish Problem.<br /><br />Some commenters on this site feel that "Watch" sags under the weight of stale propaganda. Maybe. However, neither my friend nor Pat Buchanan seem to have gotten the film\'s point: Some people hurt and kill to grab other people\'s land, goods, and liberty; such people dominated the Axis Powers and "enough" didn\'t appear in their vocabulary.<br /><br />Paul Lukas deserved the Oscar he won. He and Bette Davis put convincing passion into their portrayals of refugees who fight oppressors. They give emotional punch to the intellectual case for stepping off the sidelines, for actively facing down torturers and murderers. Bernard Dick notes that Hellman didn\'t care for Lukas as a person since he stayed apolitical. Of course, as a Hungarian he had seen first-hand Bela Kun\'s bloody "dictatorship of the proletariat" replace an outmoded empire and then topple to Admiral Horthy\'s right-wing tyranny.<br /><br />In a marvelous cameo role added to the play by Hammett, Henry Daniell sardonically depicts a Wehrmacht officer of the class that disdains the brown shirts he serves. His Phili von Ramme would doubtless stand with Field Marshal Rommel in 1944 during the Plot of July 20th against Hitler. In April 1940, however, he pragmatically abets the Nazi cause, although he insults Herr Blecher "the Butcher" and scorns the Rumanian aristocrat Teck de Brancovis for trying to peddle information on an Underground leader.<br /><br />Teck, a pauper and possible cuckold, wishes cash and a visa to return to Europe where he can resume the shreds of a life that had come undone with the empire-shattering Great War and the greater world-wide economic Depression. He has no political convictions, no scruples about trading a freedom fighter for his own tomorrow. Mercury Theater graduate George Coulouris lends this burnt-out case\'s Old World cynicism an edge of desperate menace.<br /><br />Lucille Watson gives winsome vitality to the grasping man\'s hostess, a domineering old gal who knows her mind and gets her way--but who doesn\'t adequately appreciate her children and their achievements outside the home she controls. She and her pallid office-bound son belong to the American version of von Ramme\'s and de Brancovis\' privileged kind. However, this family hasn\'t seen ruin and never will. They\'re moneyed people who could silently advance evil simply by not opposing it.<br /><br />This mother and son might easily make choices which would reflect that complaisance toward National Socialism and Fascism which flourishes today in my friend and in pundit Buchanan. "Watch on the Rhine" has a manicured period look. Its dialogue reflects its erudite origins on the stage rather than sounding fresh from the streets. Yet Hellman and Hammett\'s film has gut-based power. Audiences still need to hear and heed its call to arms against grabbers relentlessly on the march.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('After Fatih Akins first work "Im Juli", which was fairly good, he created a really gorgeous italian family epic. Its a german movie, which is unfortunately a bad precondition, cause we rareley produce more than moderate movies ;). But this movie makes some very good snapshots of the time then. "Solino" is about a Italian immigrant who arrives in the "Ruhr" region of Germany during the 60s. The immigrant and his family then start the first Pizza restaurant in the region. The characters are excellent drawn. Especially Gigi, the main actor. You live every second, every feeling he does. His brother, played by Moritz Bleibtreu, isnt that good. Well, you just dont believe him the role. But the character is wellbalanced and fits perfectly into this script. I feel an urgent need to compare the style of this movie with the style of "The Godfather". Many people will probably hate this movie, say its boring. Not much tension? - yes, but an outrageous movie. 9 out of 10.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('WARNING! Don\'t even consider watching this film in any form. It\'s not even worth downloading from the internet. Every bit of porn has more substance than this wasted piece of celluloid. The so-called filmmakers apparently have absolutely no idea how to make a film. They couldn\'t tell a good joke to save their lives. It\'s an insult to any human being. If you\'re looking for a fun-filled movie - go look somewhere else.<br /><br />Let\'s hope this Mr. Unterwaldt (the "Jr." being a good indication for his obvious inexperience and intellectual infancy) dies a slow/painful death and NEVER makes a film again.<br /><br />In fact, it\'s even a waste of time to WRITE ANYTHING about this crap, that\'s why I\'ll stop right now and rather watch a good film.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I\'ve seen all kinds of "Hamlet"s. <br /><br />Kenneth Branagh\'s was most ambitious, Mel Gibson\'s was quick and to the point, Laurence Olivier\'s was the best - hands down. But now we come to Maximilian Schell\'s take on the Bard.<br /><br />For one, this is a dubbed version of a German TV production of William Shakespeare\'s venerable chestnut. But if there\'s a slower, more plodding, more lethargic and worse-staged version out there somewhere, it must have been acted at grade school-level. <br /><br />Having seen it on MST3K helps, with Mike and the robots taking jolly good jabs at the old boy, puncturing the profundity of black and white TV, Shakespeare and the wisdom (?) of Germans acting out an English play and making it look like an Ingmar Bergman reject.<br /><br />Of course, the best parts are the MST riffs. Best lines? "I\'m gonna unleash the Great Dane", "I don\'t think so, \'breather\'", "Meet the Beatles", "Hey, Dad, will you help me with my science project" and, my personal favorite, during a party - "Garrison Keillor\'s leaving Germany (YAAAY!!)".<br /><br />But then there\'s Schell, playing Shakespeare\'s greatest character much like a department store mannequin would, only not as expressive. No doubt he\'s a great actor, but here he comes off about as well as Paul Newman in "The Silver Chalice". Ever see that one? You GOTTA watch these two on a double-bill!<br /><br />In the end, this is one instance where it\'s true that you\'re much better off to just read the book. At least the book isn\'t dubbed by Ricardo Montalban.<br /><br />One star only for this "Hamlet"; ten stars, naturally, for the MST3K version.<br /><br />Good-night, not-so-sweet prince.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('One hour, eight minutes and twelve seconds into this flick and I decided it was pretty lame. That was right after Hopalong (Chris Lybbert) drops on his horse from a tree to rejoin the good guy posse. I was pretty mystified by the whole Hopalong Cassidy/Great Bar 20 gimmick which didn\'t translate into anything at all. Obviously, the name Coppola in the credits couldn\'t do anything to guarantee success here, even with more than one listed.<br /><br />If you make it to the end of the film, you\'ll probably wind up asking yourself the same questions I did. What exactly was the hook with the gloves? What\'s up with the rodeo scenario? Who was The Stranger supposed to represent? Why did they make this film? <br /><br />I could probably go on but my energy\'s been drained. Look, there\'s already a Western called "The Gunfighter" from 1950 with a guy named Gregory Peck as the title character. Watching it will make you feel as good as watching this one makes you feel bad. That one I can recommend.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie is about this wimpy guy who decides to become a spy for a glamorous high tech company named Digicorp. This wimpy guy, Morgan (Jeremy Northam) is unhappy with his miserable suburban life and his demanding wife so he decides to become a spy. He is suppose to go to conventions from other high tech companies and find out all the companies\' plans. Instead, Morgan finds himself attracted to a beautiful woman (played by Lucy Liu) and pretty much being double-crossed by these two companies that force him to become a double agent. How will Morgan get himself out of this? Can he trust the beautiful but mysterious Rita Foster (played by Lucy Liu)? And more importantly, can Morgan make it out alive? Wow! What a nifty movie! I was completely sucked in after 15 minutes of watching this movie. It is very suspenseful and you can feel Morgan\'s fear and confusion as he is doing his best to stay alive. The scene where they put this horrible contraption on Morgan\'s head to brainwash him is brilliantly creepy and frightening. Morgan slowly goes through a personality transformation that is not so readily apparent until you think about it after the film is finished. From a wimpy guy with bad hair and glasses, he turns into a man actively fighting for his life.<br /><br />The ending, wow, the ending is incredible! The twist is so much fun! It left me gasping and cheering like crazy! Good performances from all around, especially from Jeremy Natham, Lucy Liu and Nigel Bennett.<br /><br />I highly recommend this film!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Some might scoff, but there is actually a real art with making particularly bad films. This misses out on all fronts.<br /><br />A bunch of young people -- women with heaving breasts and continuously wet T-Shirts, naturally -- go to film "blood surfing" and end up running into a 31 foot crocodile.<br /><br />Not only was the croc obviously fake, but some of the props [notice the boat hitting the reef in particular] look like they\'ve come out of thunderbirds!<br /><br />No good, from start to finish. Don\'t see it!', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('A singularly unfunny musical comedy that artificially tries to marry the then-cutting edge rock \'n\' roll explosion with the middle-class sensibilities of a suburban sitcom. The result is a jarringly dated mish-mash that will satisfy none of the audience that went for the music, but will at least keep their parents sated.<br /><br />A quick glance at the promo write-up on the back of the video release should give some idea of the content. Tom Ewell is a drunken agent, overplayed with so little comic ability you almost expect him to bellow "hi honey, I\'m home!" The blurb sites him as "So funny in \'The 7 Year Itch\'". It sounds almost like an excuse. What other film would sell itself on the fact that a leading player was good in something else? It reads like "So funny in \'The 7 Year Itch\' ... but he\'s rubbish in this".<br /><br />Mansfield, a beautiful girl with rumoured 50-inch assets, is, unfortunately, a bargain basement Monroe with all the acting ability and comic timing of a rotting haddock. Her wooden delivery combined with Ewell\'s OTT double-takes make this a comedy partnership from Hell. For her part, the sell gives us: "[Jayne Mansfield] whose more obvious talents are the cause of many of the film\'s biggest laughs!" As you can see, a movie sold on the idea that it\'s lead has a big chest is not the most sophisticated of things. Most of this "humour" is men literally falling over themselves, their glasses cracking upon site of Mansfield, etc. Only the Freudian nightmare of a milk bottle overflowing casts doubt upon its "U" certificate.<br /><br />For the musical side, the most adenine of players are chosen. Would you really care to see Eddie Fontaine offer: "I love your eyes, I love your lips, they taste even better than potato chips" in a song called "Cool It, Baby"? Only the incendiary Little Richard breaks out of the MOR, though is forced to sing some of his more dad-friendly songs in a four-minute sequence. And how come all the acts sing without a single microphone? Attempted satires on the industry are broad and childlike in their conception.<br /><br />Technically, the picture was quite advanced, with special effects (including a ghost-like Julie London) and deluxe color (Which now looks flat and artificial. In fact, with its reds that bleed and fake-looking flesh tones, it resembles a colorised movie). Direction, though, isn\'t outstanding, and the sound quality is also quite poor.<br /><br />Perhaps it comes down to it being so old. A time when men still smoked on screen, sickeningly cute child actors made adult remarks and black servants only got to cook and dance. (All of which happen here). Yet Some Like It Hot, The African Queen, Ben Hur and many, many more stand as examples of films from the period that can still be enjoyed today, so the "good at the time" argument doesn\'t really stand up. At its heart The Girl Can\'t Help It is a cynical and patronising venture that doesn\'t bear close inspection. 4/10.<br /><br />', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Put the blame on executive producer Wes Craven and financiers the Weinsteins for this big-budget debacle: a thrash-metal updating of "Dracula", with a condescending verbal jab at Bram Stoker (who probably wouldn\'t want his name on this thing anyway) and nothing much for the rest of us except slasher-styled jolts and gore. Christopher Plummer looks winded as Van Helsing in the modern-day--not just a descendant of Van Helsing but the real thing; he keeps himself going with leeches obtained from Count Dracula\'s corpse, which is exhumed from its coffin after being stolen from Van Helsing\'s vault and flown to New Orleans. This is just what New Orleans needs in the 21st Century! The film, well-produced but without a single original idea (except for multi-racial victims), is both repulsive and lazy, and after about an hour starts repeating itself. * from ****', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I\'ve always liked Fred MacMurray, andalthough her career was tragically cut shortI think Carole Lombard is fun to watch. Pair these two major and attractive stars together, add top supporting players like Jean Dixon, Anthony Quinn, Dorothy Lamour and Charles Butterworth, give them a romantic script, team them with noted director Mitchell Leisen and you geta mediocre movie experience.<br /><br />Skid Johnson (Fred) and Maggie (Carole) "meet cute" during her visit to the Panama Canal, and spend the next few weeks falling in love. Skid\'s a great trumpeter, so he embarks on a musical career, which is predictably meteoric in both its rise and fall. During his climb to musical stardom, he neglects Maggie, who later inspires him to start over after he\'s hit rock bottom. Ah, yesit\'s the true Hollywood happy ending, which comes none too soon.<br /><br />Stars and a director of this caliber should guarantee success, but this movie is so predictable and slow-paced that it\'s difficult to watch at times. The early scenes set in Panama are so draggy that they seem to go on forever, and later an alcoholic Skid just wanders endlessly in New York. Fred and Carole try their best, but the tired script and S-L-O-W direction just don\'t give them a chance. Even the final scene, in which Maggie encourages Skid to rise from the ashes of alcohol and disappointment, just doesn\'t ring true.<br /><br />This movie should be seen once to watch some early performances from stars MacMurray and Lombard. However, I guarantee that watching it will seem to take about 48 hours.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('good movie, good music, good background and an acceptable plot. but the main point again as his movies tend to be, the man is the best actor in idia and can turn dust into gold. nana patekar. this may be his second best performance after parinda( others may disagree). although other movies are not far behind. one man that will never ever disappoint you.<br /><br />good movie although i think shahrukh was a luxury this movie could have done without. you can see in his movies, others try very hard to reach his heights and act out of their skins. but this man is really something elase.<br /><br />the movie is cool, the music and direction is excellent plot a bit thin but the screen play and dialog again very good. a must watch.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('LES CONVOYEURS ATTENDENT was the first film I saw in 2000 and I doubt I\'ll see a better one this year. This beautiful tragicomedy by Belgian filmmaker Benoît Mariage is set in the industrial wastelands of Wallonia. Benoît Poelvoorde plays a father who desperately wants his son to win a car (a Lada!) for him. To do this the son has to break the record opening doors. What the father actually wants his for his son to be someone, because he himself has never made it further as the reporter of local news for a newspaper ironically called L\'Espoir (Hope). Of course nothing works out as planned. This film can best be compared to Aki Kaurismäki\'s DRIFTING CLOUDS, although it is more dramatic and the humour is darker. Just like in that film however the tone is more melancholic than depressing and the ending upbeat, without being unrealistically happy. The humour is absurd, without making the plot unbelievable, and Mariage finds stunning images in the bleak settings that never seem artificial. The best thing about LES CONVOYEURS ATTENDENT is the acting by Poelvoorde. This actor shot to fame with the also brilliant cult-classic C\'EST ARRIVÉ PRÈS DE CHEZ VOUS in which he played the charismatic hitman Ben. Since then he only played two small roles in films that were not released in the Netherlands, because, as he said in an interview, he was not convinced of his own acting capabilities and all the roles he was offered were reprises of the Ben character. With his return to a leading role in LCA there should be no doubt anymore about his acting. He\'s simply brilliant as a man stupid and evil enough to put his family in misery, but smart enough to realize what he\'s done and be torn by remorse about it. A must see.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('THE MATADOR (2005) *** _ Pierce Brosnan, Greg Kinnear, Hope Davis, Philip Baker Hall, Dylan Baker. Brosnan gives one of his best non-Bondian roles as a middle-aged assassin facing a mid-life crisis while on assignment in Mexico where he befriends a square yet likable American businessman (Kinnear at his most affable) and discovers there is more to life than death. Newbie filmmaker Richard Shepard makes a solid big screen debut with a pointedly wicked black comedy with a sharp eye for visual detail and nuanced dialogue and character development that makes him a talent to watch in this breath-of-fresh-air into the \'buddy comedy\' formula skewering what is anticipated of his leads and allowing Brosnan to get his ya-yas out with devilish glee. A sleeper gem indie hit.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This serial is interesting to watch as an MST3K feature, but for todays audience that\'s all it is. I was really surprised to see the year it was made as 1952. Considering that fact alone makes this a solid (lowly?) 2 in my book. The cars used don\'t even look contemporary, they look like stuff from the 30\'s. It\'s basically Cody (the lone world\'s salvation? Sheesh talk about an insult to everyone else, like the military), anyway it\'s Cody in his nipple ring flying suit against Graber and Daley two dumb*ss henchman who sport handguns and an occasional ray gun thats pretty lame in its own right, enjoy. If you want to watch a really good serial see Flash Gordan, it\'s full of rockets that attack each other and a good evil nemesis and also good looking women, this has NONE of that. And Flash was made 15 or so years before this crap so you can give it some slack. Something made in 1952, this bad, deserves a 2. Nuff said. give it a 6 if your watching it as a MST3K episode, those guys have some good fun with it; a tweak of the nipples here, a tweak there and I\'m flying! And now as an added bonus, I bring you the Commander Cody Theme song as originally sung by Joel and his two character bots Tom Servo and Crow aboard the satellite of love for episode eight The Enemy Planet:<br /><br />(Singing at the very beginning credits);<br /><br />(TOM SERVO SINGING) YOUR WATCHING COMMANDER CODY.... HE IS THE NEW CHARACTER FROM REPUBLIC,<br /><br />HE GETS IN TROUBLE EVERY WEEK... BUT HE\'S SAVED BY EDITING,<br /><br />JUST A TWEAK OF HIS NIPPLES... SENDS HIM ON HIS WAY,<br /><br />A PUMPKIN HEAD AND A ROCKET PACK.... WILL SAVE THE DAY,<br /><br />(JOEL SINGING) HIS LABRATORY IS A BOXING RING... WHEN BAD GUYS COME TO MIX IT UP,<br /><br />SOMEBODY ALWAYS GETS KIDNAPPED... AND CODY HAS TO FIX IT UP,<br /><br />HE DRINKS HIS TEA AT AL\'S CAFE... AND FLIES ALONG ON WIRES,<br /><br />HE BEATS THE CROOKS AND FLIES WITH HOOKS... AND PUTS OUT FOREST FIRES,<br /><br />(CROW SINGING)<br /><br />BAD GUYS BEWARE... CODY IS THERE,<br /><br />YOU\'LL LIKE HIS HAIR IT\'S UNDER HIS HELMUT... AND BECAUSE WE CAN\'T THINK OF A GOOD RHYME,<br /><br />THAT\'S THE END OF THE COMMANDER CODY THEME SONG... SO SIT RIGHT BACK WITH A WILL OF GRANITE,<br /><br />AND WATCH CHAPTER EIGHT, CAUSE THAT\'S THE ENEMY PLANET', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('After the success of Part 4, another sequel was a natural move. However they should have stopped it before it began. Alice, having survived Part 4 finds herself pregnant and it seems Freddy is using her unborn child to get at his victims, which of course are Alice\'s friends. Strange Nightmare movie, very heavy on religious imagery and bad acting. The special effects are good, but the movie itself is not.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie had a IMDB rating of 8.1 so I expected much more from it. It starts out funny and endearing with an energy that feels spontaneous. But before the movie is half-way through, it begins to drag and everything becomes sickingly predictable. The characters in the office were delightful in the first third of the movie, but we get to know them a little too well; they become caricatures, not real people at all. This is the same story I\'ve seen hundreds of times, only told here with slightly different circumstances. The thing is, I could stomach another predictable love story if only the dialog weren\'t so stale!<br /><br />The only thing that could be worse is if the characters had inconsistent and unbelievable motivations, and unfortunately that was also the case with Dead Letter Office. Hopefully this movie will end up in the Dead Movie Office soon.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This movie is spoofed in an episode of Mystery Science Theater 3000. I think MST3K was at its best when they ripped this movie.<br /><br />Terrible acting, bad makeup, poor effects, chick in skimpy (1960\'s)underwear. I give it a 2.<br /><br />The villain is hard to understand due to the makeup. The assistant says things like \'not you\' that sound like NACHOO!! (think sneezing). It\'s just poor oration. The long eyebrows are hilarious on one of the characters. <br /><br />I still don\'t know what \'The Projected Man\' means in terms of the plot. I missed some of the beginning though. <br /><br />What is up with this 10 line minimum on posting??', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('One of my favorite scenes is at the beginning when guests on a private yacht decide to take an impromptu swim - in their underwear! Rather risqué for 1931!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('"Bend It Like Beckham" is a film that got very little exposure here in the United States. It was probably due to the fact that the movie was strongly British in dialogue and terminology and dealt a lot with football, (soccer here), which some may have trouble relating too in the U.S. It\'s unfortunate because this movie is absolutely fantastic and deserved much more coverage over here. I think the basis of the storyline, (following a dream), is something many people can relate to and in the end, "Bend It Like Beckham" proves to be a good-feeling film with a source of inspiration and really good acting. I was not overly excited about seeing this film initially but now I regret not seeing it sooner. I highly recommend this movie!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Hilariously obvious "drama" about a bunch of high school (I think) kids who enjoy non-stop hip-hop, break dancing, graffiti and trying to become a dj at the Roxy--or something. To be totally honest I was so bored I forgot! Even people who love the music agree this movie is terribly acted and--as a drama--failed dismally. We\'re supposed to find this kids likable and nice. I found them bland and boring. The one that I REALLY hated was Ramon. He does graffiti on subway trains and this is looked upon as great. Excuse me? He\'s defacing public property that isn\'t his to begin with. Also these "great" kids tap into the city\'s electricity so they can hold a big dance party at an abandoned building. Uh huh. So we\'re supposed to find a bunch of law breakers lovable and fun.<br /><br />I could forgive all that if the music was good but I can\'t stand hip hop. The songs were--at best--mediocre and they were nonstop! They\'re ALWAYS playing! It got to the point that I was fast-forwarding through the many endless music numbers. (Cut out the music and you haver a 30 minute movie--maybe) There are a few imaginative numbers--the subway dance fight, a truly funny Santa number and the climatic Roxy show. If you love hip hop here\'s your movie. But it you\'re looking for good drama mixed in--forget it. Also HOW did this get a PG rating? There\'s an incredible amount of swearing in this.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This is not a "loose", but a precise, faithful remake of 1958 Monicelli\'s classic "I Soliti Ignoti" with Toto\', Mastroianni, Gassman, Cardinale etc. And that\'s the reason is good, it copies all the funny characters and the plot, even in details (like the scene where the photographer steals the camera from the local market).<br /><br />I have watched the superb old version many times and I knew by heart all the gangs and the ending but I still enjoyed "Welcome to Collinwood", which has its own freshness and atmosphere. It is interesting to see how the life and ways of the little thieves in 1950\'s Italy are adapted to 2002\'s USA. Things haven\'t changed much. 8/10.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
]


The `train_model` function is defined, which fits the training data to the pipeline, more specifically the untrained `TextCategorizer` pipeline component.The function accepts the following parameters:
- **data** is the training data that will be used to update the pipeline.
- **n_iter** is the number of times that the training data will be fed to the pipeline for training.

The function first shuffles the passed training data, as well as the `Optimizer` used by the model is gotten by calling the pipeline's `begin_training` method.

A list of numbers, starting from 0 with the length specified by the `n_iter` parameter, is initialized using the built-in Python function `range`. This is iterated over with a for-loop.

For each iteration of the loop, an empty `losses` dictionary is created. This will hold the amount of "errors" the pipeline component is making during training. It can be observed that the losses value should go down during each iteration of training to signify that the model is "learning" until it settles into a value near zero, meaning that the model has converged and is "done learning."

For each epoch, each text in the training data is iterated through. For each text value, a `Doc` is generated, but the text is not yet run through the `TextCategorizer` component. This is done using the `make_doc` method. This generated `Doc` is used to make an `Example` object, using the static method `from_dict`, that is stored alongside the "golden standard" sentiment labels that is in the training data.

Once the `Example` is made, pipeline is updated using its `update` method. It accepts a list of `Example` objects, though in this case, it is passed a list containing only a single `Example`. Alongside the list of `Example`s, the `losses` dictionary is passed which will be updated with the training's losses score, as well as the optimizer that will be used by the model. A `drop` rate of `0.1` is used to regularize the model through randomly dropping out features during training, preventing it from becoming too dependent on specific features and helping it generalize.

In [4]:
def train_model(data, n_iter = 10):
  random.shuffle(data)
  optimizer = nlp.begin_training()
  
  for epoch in range(n_iter):
    losses = {}
    for text, annotations in data:
      doc = nlp.make_doc(text)
      example = Example.from_dict(doc, annotations)
      nlp.update([example], losses=losses, sgd=optimizer, drop=0.1)

    print(f"Epoch {epoch+1}/{n_iter} - Losses: {losses}")

Once the `train_model` function is defined, it is passed the `train_data` list, as well as specified how many iterations the training will do.

In [5]:
train_model(train_data, n_iter=10)

Epoch 1/10 - Losses: {'textcat': 27.637468576431274}
Epoch 2/10 - Losses: {'textcat': 16.302733560497472}
Epoch 3/10 - Losses: {'textcat': 2.190791864064538}
Epoch 4/10 - Losses: {'textcat': 1.6242055461924947}
Epoch 5/10 - Losses: {'textcat': 0.18118287489958418}
Epoch 6/10 - Losses: {'textcat': 0.6553127158385691}
Epoch 7/10 - Losses: {'textcat': 0.03858749231648515}
Epoch 8/10 - Losses: {'textcat': 0.037221468451602784}
Epoch 9/10 - Losses: {'textcat': 1.981668649969628}
Epoch 10/10 - Losses: {'textcat': 0.9237489188126119}


Once the pipeline is trained, a `predict_sentiment` function is defined that takes in a `text` that will be used to predict its sentiment, whether it is `POSITIVE` or `NEGATIVE`.

This is done by calling the trained pipeline and passing the text to it. This returns a generated `Doc` that holds the probabilities of each label in the its `cats` attribute. These probabilities are then returned by the function.

In [6]:
def predict_sentiment(text):
  doc = nlp(text)
  return doc.cats

To test the model, the user is asked for an input by using Python's built-in `input` function. This accepts a string that will be be prompted to the user when asking for input. The function then returns the text that the user gave.

This `user_input` is then fed to the previously-defined `predict_sentiment` function and the returned label probabilities are stored and displayed to the user.

In [35]:
user_input = input("enter a text for sentiment analysis: ")
prediction = predict_sentiment(user_input)

print("\nSentiment prediction")
print(prediction)


Sentiment prediction
{'POSITIVE': 0.0, 'NEGATIVE': 0.0}


To evaluate the model, the `evaluate` function is defined which accepts a single parameter `data` which holds the testing data.

A list of `Example`s are first created using Python's list comprehension feature, which is done by iterating through the given `data` parameter. The text is passed to the trained pipeline, while the "gold standard" sentiment labels are passed as reference.

A list of actual and predicted values are generated using list comprehension, which are stored in `y_true` and `y_pred`, respectively. This is done by iterating through the list of `Example` objects and fetching, either the `reference` document for `y_true`, or the `predicted` document for `y_pred`. If the value of the `POSITIVE` label is greater than the `NEGATIVE` label then the element is set to one (1), else it is set to zero (0).

The metrics is then generated and displayed using the `classification_report` method. This displays the Accuracy, Prediction, Recall, and F1-Score of the predicted labels.

In [7]:
def evaluate(data):
  examples = [Example.from_dict(nlp(text), annotations) for text, annotations in data]
  y_true = [1 if example.reference.cats['POSITIVE'] > example.reference.cats['NEGATIVE'] else 0 for example in examples]
  y_pred = [1 if example.predicted.cats['POSITIVE'] > example.predicted.cats['NEGATIVE'] else 0 for example in examples]

  print("Classification Report:\n", classification_report(y_true, y_pred))

The testing data for the evaluation of the trained sentiment analysis model is loaded. It contains a subset of data found in the [`stanfordnlp/imdb`](https://huggingface.co/datasets/stanfordnlp/imdb) dataset.

In [11]:
test_data = [
  ('I could not believe how terrible and boring this Hollywood remake was.It\'s so dreadful. It easily lands a place in my top 10 worst films of 1998.About the only thing it had going for it was Bruce Willis,who should stick to action films,as a completely emotionless killer who\'d kill his own mother for the right price.But I\'d rather listen to Robbie Coltraine talk American for a week than listen to Richard Gere\'s nauseating Irish accent again.But this film is also implausible,unconvincing,uneven,unexciting,unimpressive and lands Sidney Poiter in a rubbish role to make a possible career comeback.One for filmroll-footie purposes entirely.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I rented Boogie Nights last week and I could tell you, when I watched the film I had a blast. If you think that when you watch the film you will get sicked by the porn. I mean yes, if your not a porn person who can\'t bother being by it, than this isn\'t the film to see. But the thing is, the whole film isn\'t really about porn. Well halfway through the film is about the porn industry but the other half is about the character development and the bad situations these characters go through. The actors played there roles perfect, especially Mark Wahlberg, John C. Reilly, and William H. Macy. The sex scenes, of course are terrific but mainly focus on the character\'s hype in porn films until there struggles. Excellent film, one of the best! <br /><br />Hedeen\'s Outlook: 10/10 **** A+', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('First off, this movie is not near complete, my guess is that someone actually bothered to steal every other page of the script.<br /><br />The movie contains bizarre time-travels without notice, inconsistent dialogs, misplaced details all over, the music isn\'t very bad at all, other then misplaced tracks, and besides the fact that the volume goes up and down between the different tracks. The cutting-room did a descent job actually, and that says a lot. Missplaced sound effects ruin the tension, though.<br /><br />Luke Perry does what he does best, just looking worried, and occasionally coughing up punchlines from hell.<br /><br />I seriously rate this movie as the worst of 2007, and i\'ve seen a few bad ones. Do not spend money on this one, it\'s not so bad it\'s a laugh, it\'s worse. Ratings above 1 star, should render a blacklist at IMDb, because it\'s a damn lie.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I watched this mini in the early eighties. Sam Waterson proved himself to be a great actor. In fact when he began Law and Order I was disappointed in him as it was not as powerful a role. Unfortunately the good roles do not pay the bills. I wish I could find a copy of this rare series and review it. It is both factual and entertaining. Everyone should see it to know what really happened. I was so moved I purchased and read the book "Pppenheimer-Shatterer of Worlds". And saw how this man became an unlikely hero who was never rewarded for his insight. If you get a chance be sure to watch this movie and see what a performance Mr. Waterston can really provide an audience. Enjoy the movies!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('This movie was never intended as a big-budget film but was a cute little picture that pretty much anyone could enjoy. It probably won\'t change your life, but it is certainly charming and engaging.<br /><br />Clifton Webb plays a curmudgeon (that\'s certainly not new) who has a TV. However, his ratings are failing and he is worried about cancellation. So he decides maybe he is too out of touch with kids--as he and his wife have none of their own. So, he volunteers as a scoutmaster and regrets doing this almost immediately! Remember, he IS a curmudgeon and doesn\'t particularly like kids. To make things worse, one of the kids really likes him and follows him like a lost puppy. No matter how indifferently he acts towards the kid, the child just wants to spend time with him! The kid is cute and nearly steals the show all by himself! <br /><br />What happens next and the twists and turns of the movie are something you\'ll just have to find out for yourself. Understand that this is a light, cute and yet not cloying movie you\'ll probably enjoy.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I thought this was an extremely bad movie. The whole time I was watching this movie I couldn\'t help but think over and over how bad it is, and how that was $3.69 down the drain. The plot was so jumpy. They did an excellent job at the beginning of explaining who dated who in high school, but they never really explained anything after that. Was it a supernatural thriller? Was it a regular thriller? Apparently you can decide for yourself, because they didn\'t see the need to explain. I understood basically what happened, I think. What I got confused about was all of it prior, what was the deal with the bloody noses, phone calls, etc.? Was this guy coming back? Was the wife channeling "Carrie" or something? Who knows? You certainly won\'t after watching this movie.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This was one of the biggest pieces of crap I have ever had to watch. I mean, seriously. How would anybody else feel if they were in Woody Harrelson\'s shoes and your wife was even CONSIDERING it would be a good idea to sleep with the other guy even for a million bucks. After all, she was the one talking about it in bed and saying how it would be good for them since he can build his house or whatever with that money. Woody never fully agreed to it until she talked him into it. How CAN you trust her? Who the hell would actually even consider that if they were married? I don\'t care how desperate they were. That\'s the most ridiculous thing I have ever heard in my life. Then, he flips out on her. Apparently, he had no right to mistrust her, other than the fact that his wife just slept with another dude who is extremely rich and handsome. Oh and wait, then he\'s supposed to apologize to HER after she files for the divorce so she can be with the guy she slept with. Of course Woody has no right to say anything to her or mistrust her especially after she still has Roy Hobb\'s card in her wallet. Then, at the end of the movie, she\'s apparently so in love with Woody still and misses him so much, that she was not going to leave Hobbs until he made some ridiculously stupid story up to try to hint to her to leave, and she bleeping thanks Hobbs???? Are you bleeping kidding me? Was she under contract as his sex slave or something?? I mean what the bleep?? Oh and wait it gets better. She bleeping kisses him passionately before she gets out of the car. Yea, she\'s not a whore. Oh, thank you for letting me go, let me go make out with you one last time for good ole\' sake. Smooch smooch, smooch even though I\'m still married to a guy I left for a rich guy. I have never seen such a piece of crap in my life. How the hell are we supposed to feel good after that horrible ending? What was this movie supposed to represent? NOTHING CAME OUT OF THIS! This was the most pointless movie I have ever seen in my life. Two pathetic desperate people. If I were Woody, I would tell her to go drown herself in that body of water they were near. Apparently, he had no self respect. What the hell was Roy Hobbs thinking by taking this horrible role. I feel like puking after watching this. This movie was so bad, it was seriously laughable. I want those two hours of my life back that I wasted watching this piece of ****.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I just watched it for the second time today and I must say with all my heart it is about damn time they made a movie about us as people not as spiritual beings. Such a waste of human life as this story was maybe some good will come out of it. And Eric is hotter than ever. To often in the movies First Nations people are seen as other than everyday people. We are always portrayed as chiefs or medicine people. Hey we are just like everyone else. And this movie showed just that. We hurt when an injustice is done and we can win in quest for justice. It is really to bad that the big movie companies cant see that. I cant wait till this comes out on DVD. Thanks to those who chose to show this story as it really was.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I\'ve read through a lot of the comments here about how this movie sticks to the book.. I don\'t think any of them have actually read it. Edgar Rice wrote about a dangerous African Jungle and Apes were killers and hunters. We know differently now and this movie portrays Apes in a more modern view. I\'ve never seen a Tarzan movie that even comes close to Edgar\'s vision. Maybe one day Hollywood with trust talented and respected authors to tell the story. So, if you\'ve never read the book and enjoy a good story about feelings and a fluffy bunny view of wild animals, maybe a good cry, see the movie. I hope John Carter of Mars get\'s more respect than Tarzan has. We miss ya, Edgar!', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('I usually much prefer French movies over American ones, with explosions and car chases, but this movie was very disappointing. There is no way to write a spoiler because nothing really happens. This French couple has been living in Lisbon for years, and they return to Paris for a friend\'s wedding. They announce to another friend they are having dinner with that they are going to split. Then nothing much happens, they don\'t seem to know whether they want to separate or not. I don\'t necessarily think that their hesitations make for a bad movie, it is very human to hesitate before making such a decision for good, but this could be treated in an interesting manner, giving some flesh to their desires and their relationship, but that does not happen. One gets out of the theater unsure of why these two got together or want to split. The only piece I enjoyed was the conversation with the drunk. That was true to life.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('This was very funny, even if it fell apart a little at the end. Does not go overboard with homage after to Hitchcock - Owen (Danny DeVito) was lucky he had "Strangers on A Train" playing at the local cinema, so the movie flat out tells you that that was the inspiration. <br /><br />DeVito is very funny but also a little sad. He has no friends and all he wants to do is write and have someone like his writing. His teacher, Billy Crystal, is going through some serious writers block of his own and his wife has stolen his book and made it her own success, which also has him frustrated a great deal.<br /><br />Best parts are the book proposal by Mr. Pinsky ("One Hundred Girls I\'d Like to Pork") and all scenes with Anne Ramsey, who is so horrible that even Mother Theresa would have wanted to kill her, too!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('SPOILER!!!! Mind Ripper hmmmm.... I had just watched the nightmare on elm street movies and had just found out about Giovanni Ribisi. I thought Giovanni Ribisi hadnt done any horrors so I checked into it. I saw "the outpost" (mind ripper) I checked on my Tivo for it. There was an air date on Sci Fi. So I was set. I got my pop corn ready came in and set on the couch and what the hell is this? A freakin bold guy in blue sweat pants running around yelling! Nothing is scary about this movie at all! If anything its funny! Funny how low the budget is, funny how predictable it is, funny how bad the acting is and funny how much money it DIDNT make. Ok giovanni ribisi is a good actor but this movie is dumb. It is so stupid. They killed him at the end and then they go on this plane and the "monster" is on it. They shoot him in the head with a shotgun and it falls a long way to the ground. And<br /><br />-GASP- The killer ending, Its Still Alive! WOOHHH! Scary! woooohhhh! Sucky fat sack of crap waste of 2 hours.<br /><br />Bottom Line: You have somewhere to go and you need to kill some time. Mind ripper isnt the suggestion. I\'d rather sit out naked in the snow than watch this movie a second time.<br /><br />OVERALL GRADE: F- - - - - - - - - - (ENTERNAL)', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Some folkie friends recommended this, but as a film it\'s really lacking in originality. I found the characters to be unflattering stereotypes, and the plot is predictable almost from the beginning. However, if you like traditional English/Appalachian ballads, it will keep your interest long enough to hear the next one. I\'ve also read that the soundtrack is nothing like the music in the movie, with professional musicians filling in for the actors.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('From 1950 comes a neat thriller about a couple smuggling diamonds from abroad and also the contagious disease smallpox. Evelyn Keyes pulls out all stops as the essential victim of this film-noir. Once back in the United States she is not aware that she could be spreading the disease on everyone and everything she comes in contact with. Eventually she is pursued and must be stopped before an epidemic occurs. Other than Keyes striking performance there is good support from villainous Charles Korvin, William Bishop, Dorothy Malone, Lola Albright and Whit Bissell. The finale is a humdinger with Miss Keyes on the ledge of a building with spotlights and hundreds of spectators below. A good B flick!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('I cannot believe I actually sat through the whole of this movie! It was absolutely awful, and totally cringe-worthy, and yet I sat through it thinking it had to get better. It didn\'t, and I have wasted 2 hours of my life. Will Smith is much better in action movies - I loved him in I, Robot, Enemy of the State and Independence Day - and I don\'t think he can really be expected to carry off an entire movie as the romantic lead in the way that Cary Grant could. Then again, the script was unbearably awful, and the dialogue was so cheesy. <br /><br />I disliked everyone except for Albert\'s character, and even that I found was done with a heavy hand. If you want to watch a modern feel-good romantic comedy, watch something like How To Lose A Guy In Ten Days, or When Harry Met Sally. The 40 Year Old Virgin left me with a smile on my face. I even preferred Music and Lyrics above this - and yes, I know it\'s cheesy, but at least it didn\'t take itself seriously, and was sweet. I also disliked the main female lead - and wasn\'t convinced of the chemistry between her and Will Smith\'s character. <br /><br />In all, I think there were two scenes that I liked (and definitely not the ending, which was nauseating and unconvincing!) - Hitch calling Sarah when she hadn\'t given him her number was quite sweet, and - no, sorry, that\'s the only thing I liked about the entire film. Don\'t waste your time.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('The movie was very good. I\'m an avid mystery fan and I usually figure out who is going to be killed and who did the killing. While I did figure out who was going to be killed I didn\'t figure out who did it. I wasn\'t happy with the portrayal of the Gerda character but given the year the movie was supposed to take place it is possible the woman would have been that \'cloying\'. Please know that while these Poirot movies are good, they just don\'t have the same dynamic to them as the series does because they don\'t have Japp, Ms. Lemon and especially Hastings! David Suchet is definitely Poirot. I have seen every actor who\'s played him. The worst was Peter Ustinov!', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Hitchcock would be proud of this movie. Even when nothing happens, it is suspenseful. Director David Lynch overuses a few cheap thrill tricks here and there, but he intersperses them with other cinematographic techniques to keep it from becoming obtuse.<br /><br />Altogether surreal, this movie is like waking up and remembering most of a dream but not enough to make it sensible. I am still trying to figure it all out and will probably have to see it again to catch things I missed and which may help me understand it better. It is a very detailed plot that very slowly comes together, so you must be patient and pay attention. Get your bathroom trip out of the way before it starts. And yet, the plot is overshadowed by the theme, the mood, the character development, and the filming techniques.<br /><br />The dual roles of the main actress, Naomi Watts, showcase her enormous talent. That is, when I could get my eyes off of her co-star. What an acting pair.<br /><br />Lynch surprises throughout the movie with unusual camera angles, the length/timing of editing cuts, jumping back and forth between scenes. Combined with smart use of music and sounds, it all helps to build suspense in our minds, doubtless a major objective of the director. Well, he kept me on the edge of my seat, even had me talking to the actors to be careful here, and not be so naive there. You know, the kind of stuff you want to smack your kids for doing at the movies.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('OK. So it can be done! We have here the perfect vampire movie. Gothic, beautiful. With all the ingredients. A realistic vampire. A wonderful story. Take note - I am from Transylvania and I assure you, this movie respects the vampire lore! It\'s exactly like the tales I heard in my childhood. For a transylvanian, it is quite... believable. You must see it, if you are interested by real vampires, as they were depicted in medieval chronicles and not how are they done in recent Hollywood movies (as far as I can guess, the Hollywood problem is they mix vampires with the incubus - which is pretty hilarious for me. Vampires are never good-looking or attractive, they can inspire only horror and repulsion. The incubus - called in my country The Night Flier, is the one beautiful demon which kills his victims by loving them.) I strongly recommend this for any Gothic person out there! See also the sequels, they are all 4 very good! And of course, don\'t miss DArk shadows! Something similar is Nosferatu In Venice with Klaus Kinski. I recommend that one to.', {'cats': {'POSITIVE': 1, 'NEGATIVE': 0}}),
  ('Licence fees to watch this trash, And pay for it with hard-earned cash? Humourless, no hint of laughter, God knows how it won a BAFTA! <br /><br />We\'ve now been subjected to "Eastenders" for twenty years. When, oh when is the Great British public going to see this awful soap for what it is? Crass Pap! This programme no more depicts reality in the East End of London than everyday life in Beirut, and never has done.<br /><br />The Eastenders I know (the real ones) are kind, courageous, hardworking and loyal. And one of their greatest attributes is humour. It was the Eastenders who went through the worst of the London blitz and still stuck two fingers up to Hitler. And what do we see on our screens for five days of the week (including an omnibus)? Nothing but a bunch of moaning, wailing, "dead from the neck up" wimps, who seem to do little else than sit in a pub all day sniping at each other. What a great advert for Britain that is!! Do the writers actually believe this garbage they\'re pumping out? Obviously the woolly-minded section of the public does, but then I\'ve heard that apparently anyone can be brainwashed into believing anything.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
  ('Hadn\'t really heard too much about this movie so I went and saw it. I realized that this movie only appeals to someone who has not lived in the real world. And even those people would think this movie moved too slowly.<br /><br />When the movie opens up, you see Nicole Kidman going to a nudist camp. Whoa. Shock. That scene, the dialouge, were all great. And then the movie went downhill.<br /><br />While I respect the vision the filmmaker must have, this movie sucked. It was too slow, too predictable, and not moving enough. Robert Downey Jr. is great, as usual, but this movie is not good enough to sit through. It tries to be shocking and abnormal but makes poor use of the talents of all the actors.<br /><br />Don\'t waste your money, even the sex scenes were boring.', {'cats': {'POSITIVE': 0, 'NEGATIVE': 1}}),
]

Once the test data is loaded, it is passed to the previously-defined `evaluate` function, which then subsequently display the performance of the trained sentiment analysis pipeline.

In [12]:
# print("Training Data Performance:\n")
# evaluate(train_data)
print("Testing Data Performance:\n")
evaluate(test_data)

Testing Data Performance:

Classification Report:
               precision    recall  f1-score   support

           0       0.73      0.73      0.73        11
           1       0.67      0.67      0.67         9

    accuracy                           0.70        20
   macro avg       0.70      0.70      0.70        20
weighted avg       0.70      0.70      0.70        20



# Text Summarizer

For the text summarizer process, the following libraries were used:
- **spaCy** is used for its pipelines and functionalities that allow for analysis of text data.
- **collections** is a built-in Python library that contains specialized container datatypes. For this implementation, the `Counter` datatype is used, which is a dictionary subclass for counting the occurences of objects.
- **rouge_score** is a library that implements a native Python implementation of ROUGE scoring.

In [1]:
import spacy
from collections import Counter
from rouge_score import rouge_scorer

The first step in the part-of-speech tagging process is the loading of the language pipeline. `en_core_web_sm` is a pre-trained pipeline for the English language which includes the pipeline components `tok2vec`, `tagger`, `parser`, `senter`, `attribute_ruler`, `lemmatizer`, and `ner`.

For the purposes of this implementation, only the results of the `lemmatizer` component and the pre-trained `Vocab` object will be analyzed, but the effects of the other components are included in the generated `Doc` object.

In [2]:
nlp = spacy.load('en_core_web_sm')

This defines the text that will be summarized by the text summarizer process, as well as the "gold standard" summary of it. This data is a single entry from the [`abisee/cnn_dailymail`](https://huggingface.co/datasets/abisee/cnn_dailymail).

In [3]:
article_and_summary = (
  "LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in \"Harry Potter and the Order of the Phoenix\" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties. \"I don't plan to be one of those people who, as soon as they turn 18, suddenly buy themselves a massive sports car collection or something similar,\" he told an Australian interviewer earlier this month. \"I don't think I'll be particularly extravagant. \"The things I like buying are things that cost about 10 pounds -- books and CDs and DVDs.\" At 18, Radcliffe will be able to gamble in a casino, buy a drink in a pub or see the horror film \"Hostel: Part II,\" currently six places below his number one movie on the UK box office chart. Details of how he\'ll mark his landmark birthday are under wraps. His agent and publicist had no comment on his plans. \"I'll definitely have some sort of party,\" he said in an interview. \"Hopefully none of you will be reading about it.\" Radcliffe's earnings from the first five Potter films have been held in a trust fund which he has not been able to touch. Despite his growing fame and riches, the actor says he is keeping his feet firmly on the ground. \"People are always looking to say 'kid star goes off the rails,'\" he told reporters last month. \"But I try very hard not to go that way because it would be too easy for them.\" His latest outing as the boy wizard in \"Harry Potter and the Order of the Phoenix\" is breaking records on both sides of the Atlantic and he will reprise the role in the last two films.  Watch I-Reporter give her review of Potter's latest » . There is life beyond Potter, however. The Londoner has filmed a TV movie called \"My Boy Jack,\" about author Rudyard Kipling and his son, due for release later this year. He will also appear in \"December Boys,\" an Australian film about four boys who escape an orphanage. Earlier this year, he made his stage debut playing a tortured teenager in Peter Shaffer's \"Equus.\" Meanwhile, he is braced for even closer media scrutiny now that he's legally an adult: \"I just think I'm going to be more sort of fair game,\" he told Reuters. E-mail to a friend . Copyright 2007 Reuters. All rights reserved.This material may not be published, broadcast, rewritten, or redistributed.",
  "Harry Potter star Daniel Radcliffe gets £20M fortune as he turns 18 Monday . Young actor says he has no plans to fritter his cash away . Radcliffe's earnings from first five Potter films have been held in trust fund .",
)


To do the text summarization process, the `summarize` function is defined. This function in the following parameters:
- **text** is the text that will be summarized.
- **n_sentences** is the number of sentences that will be composed for the summary.

The first step in the text summarization is done by passing the text to the pre-trained pipeline, which returns a generated `Doc`. An empty `sentence_scores` counter is also created, that will hold sentences from the given text.

Each sentence in the generated `Doc` is then iterated through, where each token is in the sentence is also looped over.

For each token, it is checked if its not a stopword (using the `is_stop` attribute) and if its not a punctuation (using the `is_punct` attribute). If it passes both condition, the sentence that the token belongs to has its count in `sentence_scores` counter is incremented by one (1).

Once all sentences have been iterated through, the top sentences are gathered by the using the counter's `most_common` method. This takes in a parameter which tells how much entries should be returned. For this implementation, this is dictated by the value of the `n_sentences` parameter, which by default is two (2). These top sentence are then returned.

In [4]:
def summarize(text, n_sentences=2):
  doc = nlp(text)
  sentence_scores = Counter()

  for sent in doc.sents:
    for token in sent:
      if not token.is_stop and not token.is_punct:
        sentence_scores[sent] += 1

  top_sentences = [sent.text for sent,score in sentence_scores.most_common(n_sentences)]
  return " ".join(top_sentences)

To demonstrate the text summarizer, the user is asked for an input using the built-in Python `input` function, where the given string parameter is the text that will prompted to the user.

The returned string from the user is passed to the `summarize` function which returns the generated summary. This summary is then displayed to the user.

In [5]:
user_text = input("Enter the text you want to summarize: ")
summary = summarize(user_text)

print("\n Summary:")
print(summary)


 Summary:
LONDON, England (Reuters) -- Harry Potter star Daniel Radcliffe gains access to a reported £20 million ($41.1 million) fortune as he turns 18 on Monday, but he insists the money won't cast a spell on him. Daniel Radcliffe as Harry Potter in \"Harry Potter and the Order of the Phoenix\" To the disappointment of gossip columnists around the world, the young actor says he has no plans to fritter his cash away on fast cars, drink and celebrity parties.


The ROUGE scoring function is defined by creating an instance of the `RougeScorer` class. This particular scorer has three types that it will output:
- **rouge1** looks at how many words between the two text given to the scorer.
- **rouge2** looks at how many two-word sequences match between the two text.
- **rougeL** looks at the longest common subsequence (LCS) between the two text.

The `use_stemmer` parameter applies stemming to a word before it is compared. Stemming involves reducing a given word to its base form by removing suffixes. This simplifies the words further, improving the probability that two like words get compared accurately.

In [6]:
scorer = rouge_scorer.RougeScorer(['rouge1', 'rouge2', 'rougeL'], use_stemmer=True)

Once the scorer instance is created, the article and summary are prepared for evaluation. Both of them are extracted out of the tuple that stored them and are put into their own variables.

The "gold standard" summary is processed by the pipeline, such that we can lemmatize the tokens later for improved performance.

The summary of the text is generated by passing it to the previously-defined `summarize` function. Notably, the `n_sentences` parameter is set to the number of the "gold standard" summary, such that the process can be evaluated properly. This is done by getting the amount of entries found in the `sents` attribute of the generated `Doc` for the "gold standard" summary.

The result of the `summarize` function is also passed through the pipeline, after which both `Doc`s are iterated through and the lemmatized tokens are extracted and joined into a single string, which are `ref_tokens` and `gen_tokens`.

Once all tokens have been collected, they are passed to the `score` method of the scorer instance that was previously defined. This outputs a dictionary for each listed ROUGE type and their corresponding precision, recall, and f1-score. The tokens, as well as the calculated scores are all displayed to the user.



In [7]:
article, summary = article_and_summary
ref_doc = nlp(summary)

summarized = summarize(article, n_sentences=len(list(ref_doc.sents)))

gen_doc = nlp(summarized)

ref_tokens = " ".join([token.lemma_ for token in ref_doc])
gen_tokens = " ".join([token.lemma_ for token in gen_doc])

scores = scorer.score(ref_tokens, gen_tokens)

print(ref_tokens)
print(gen_tokens, "\n")
for type, metrics in scores.items():
  print(f"Type: {type}")
  print("Scores:")
  print(f"Precision: {metrics[0]}")
  print(f"Recall: {metrics[1]}")
  print(f"F1-Score: {metrics[2]}\n")

Harry Potter star Daniel Radcliffe get £ 20 m fortune as he turn 18 Monday . young actor say he have no plan to fritter his cash away . Radcliffe 's earning from first five Potter film have be hold in trust fund .
LONDON , England ( Reuters ) -- Harry Potter star Daniel Radcliffe gain access to a report £ 20 million ( $ 41.1 million ) fortune as he turn 18 on Monday , but he insist the money will not cast a spell on he . Daniel Radcliffe as Harry Potter in " Harry Potter and the order of the Phoenix " to the disappointment of gossip columnist around the world , the young actor say he have no plan to fritter his cash away on fast car , drink and celebrity party . at 18 , Radcliffe will be able to gamble in a casino , buy a drink in a pub or see the horror film " Hostel : Part II , " currently six place below his number one movie on the UK box office chart . 

Type: rouge1
Scores:
Precision: 0.24369747899159663
Recall: 0.725
F1-Score: 0.36477987421383645

Type: rouge2
Scores:
Precision: 